In [1]:
import os
import polars as pl
import pandas as pd
pl.Config(tbl_rows=100)
from src.najdi_rok import najdi_rok
from src.pocet_stran import pocet_stran
from src.bez_bordelu import bez_bordelu

In [34]:
df = pl.read_parquet(os.path.join("data/cnb_sloupce","100.parquet"))
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","leader.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","008.parquet")), left_on="001", right_on="001", how="left")
df = df.to_pandas()
df = df[df["leader"].str[6].isin(["a", "t"])]
df = df[~df["leader"].str[7].isin(["b", "i", "s", " "])]
df = df[(df["008"].str[15:17] == "xr") & (df["008"].str[35:38] == "cze")]
df = pl.from_pandas(df)
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","022.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","245.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","300.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","655.parquet")), left_on="001", right_on="001", how="left")
df = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","700.parquet")), left_on="001", right_on="001", how="left")
df = df.explode("022_a").filter(pl.col("022_a").is_null())
df = df.with_columns(pl.col('008').map_elements(najdi_rok, return_dtype=int).alias('rok'))
df = df.with_columns(pl.col('300_a').map_elements(pocet_stran, return_dtype=int).alias('stran'))
df = df.with_columns(pl.col('245_a').map_elements(bez_bordelu, return_dtype=str))
df = df.explode('245_p').with_columns(pl.col('245_p').map_elements(bez_bordelu, return_dtype=str))
print(len(df))

716107


In [35]:
df = df.filter(pl.col("rok") >= 1800)

In [36]:
print(len(df))

709460


In [37]:
df = df.filter((~pl.col("245_h").str.contains("grafika")) | pl.col("245_h").is_null()).unique(subset=["008","100_a","245_a","245_p"], keep="first")

In [38]:
print(len(df))

705250


In [39]:
nechcemejetam = [
    "jn20001103401",
    "xx0008006",
    "jn19990008769",
    "jx20060515016",
    "jn19981002230",
    "jn19981001737",
    "jn19990210182",
    "jn19990001842",
    "jn19990002786",
    "jn19990004346",
    "jn20020721077",
    "jn19990210513",
    "jn19990005488",
    "jo20000080627",
    "jn19990000171",
    "jn20001005715",
    "jn19981002409",
    "jn20000810141",
    "jn19981002129",
    "jn20001103529",
    "jn20000810032",
    "jn19990001513",
    "jx20040611003",
    "jn19990005499",
    "jn19981002230",
    "jn19990001907",
    "jo2005267810",
    "jo20241218643",
    "jn20000602144",
    "jn19990005454",
    "jn19981228078",
    "xx0010566",
    "jn20010310318",
    "xx0203193",
    "jn20001227589",
    "jo2003204270",
    "xx0082647",
    "jn19990001239"
]

# df = df.filter(~pl.col("100_7").is_in(nechcemejetam))

In [40]:
df.sample(10)

shape: (10, 69)
┌──────────┬─────────────────────────┬────────────────┬───────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a                   ┆ 100_7          ┆ 100_4     ┆ … ┆ 700_5     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---                     ┆ ---            ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str                     ┆ str            ┆ list[str] ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪═════════════════════════╪════════════════╪═══════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ Balde, Henricus,        ┆ jo2008429122   ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1931 ┆ 177   │
│ 1        ┆ Štěpánková, Marta       ┆ jk01131333     ┆ ["edt"]   ┆ … ┆ null      ┆ null      ┆ 1982 ┆ 250   │
│ 1        ┆ Červinka, Jiří,         ┆ xx0040107      ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2019 ┆ 54    │
│ 1        ┆ Sláma, František Josef, ┆ jk01111772     ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1891 ┆ 139   │
│ 1        ┆ Hlaváčková, Iva,        ┆ jn20000400967  ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2014 ┆ 360   │
│ 1        ┆ Bosák, Jaromír,         ┆ jn20000400226  ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 84    │
│ 1        ┆ Strong, Pitt,           ┆ jo2005267810   ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1940 ┆ 32    │
│ 1        ┆ Kolenička, Ján          ┆ jk01061331     ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1972 ┆ 127   │
│ 1        ┆ Řezáč, Václav,          ┆ jk01110105     ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1951 ┆ 462   │
│ 1        ┆ Janča, Štěpán,          ┆ pna20221144460 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1999 ┆ 62    │
└──────────┴─────────────────────────┴────────────────┴───────────┴───┴───────────┴───────────┴──────┴───────┘

In [41]:
df = df.drop_nulls(subset=["700_a","700_4","700_7"]).explode(["700_a","700_4","700_7"])

In [42]:
df.select(pl.col(["700_a","700_4","700_7",'245_a'])).sample(10)

shape: (10, 4)
┌────────────────────┬───────┬───────────────┬─────────────────────────────────┐
│ 700_a              ┆ 700_4 ┆ 700_7         ┆ 245_a                           │
│ ---                ┆ ---   ┆ ---           ┆ ---                             │
│ str                ┆ str   ┆ str           ┆ str                             │
╞════════════════════╪═══════╪═══════════════╪═════════════════════════════════╡
│ Kaufová, Tereza    ┆ aut   ┆ jo2012725343  ┆ Kočičí zahrada                  │
│ Mach, Bohumil,     ┆ aui   ┆ jk01072881    ┆ Píseň ženy                      │
│ Zima, Tomáš,       ┆ aut   ┆ jn20000620440 ┆ Vybrané kapitoly o zdraví       │
│ Křemenáková, Anna, ┆ trl   ┆ jk01070028    ┆ Generace                        │
│ Šrut, Pavel,       ┆ aut   ┆ jk01131041    ┆ Kráska v nesnázích              │
│ Felix, Jozef,      ┆ aui   ┆ jn19981001047 ┆ Dekameron                       │
│ Jursch, Lorena     ┆ pht   ┆ xx0317187     ┆ Soběstačnost                    │
│ Kadlec, Jiří,      ┆ aut   ┆ ntka172849    ┆ Osobní počítače I               │
│ Holeinone, Peter   ┆ aut   ┆ mzk2004258668 ┆ Dinosauřík                      │
│ Španová, Alena,    ┆ aut   ┆ uzp2009465467 ┆ Molekulární identifikace a typ… │
└────────────────────┴───────┴───────────────┴─────────────────────────────────┘

## Autorské spolupráce

In [44]:
from itertools import combinations

In [45]:
def find_collaborations(df):
    # Filter for authors only
    authors = df.filter(pl.col('700_4') == 'aut')
    
    # Group by book title to get authors per book
    books_authors = authors.group_by('245_a').agg(pl.col('700_a').alias('authors'))
    
    # Generate author pairs and count collaborations
    collaborations = []
    for book in books_authors.iter_rows():
        if len(book[1]) > 1:  # Only consider books with multiple authors
            for pair in combinations(sorted(book[1]), 2):
                collaborations.append(pair)
    
    # Convert to dataframe and count frequencies
    collab_df = pl.DataFrame({
        'author1': [p[0] for p in collaborations],
        'author2': [p[1] for p in collaborations]
    })
    
    if len(collab_df) == 0:
        return pl.DataFrame({'author1': [], 'author2': [], 'collaboration_count': []})
    
    return (collab_df.group_by(['author1', 'author2'])
            .count()
            .sort('count', descending=True)
            .rename({'count': 'collaboration_count'}))

In [46]:
find_collaborations(df).filter(pl.col("author1") != pl.col("author2"))

C:\Users\micha\AppData\Local\Temp\ipykernel_28588\3784072569.py:25: DeprecationWarning: `GroupBy.count` is deprecated. It has been renamed to `len`.
  .count()


shape: (222_076, 3)
┌─────────────────────────┬────────────────────────────┬─────────────────────┐
│ author1                 ┆ author2                    ┆ collaboration_count │
│ ---                     ┆ ---                        ┆ ---                 │
│ str                     ┆ str                        ┆ u32                 │
╞═════════════════════════╪════════════════════════════╪═════════════════════╡
│ Novotný, Miloš          ┆ Novák, František           ┆ 1165                │
│ Král, Lukáš             ┆ Valenta, Tomáš             ┆ 1156                │
│ Krupka, Peter,          ┆ Nechvátalová, Jana,        ┆ 1089                │
│ Malý, Martin            ┆ Münch, Otto                ┆ 897                 │
│ Münch, Otto             ┆ Čechová, Jarmila           ┆ 826                 │
│ Frydryšková, Yvetta     ┆ Münch, Otto                ┆ 820                 │
│ Nechvátalová, Jana,     ┆ Staudková, Hana            ┆ 792                 │
│ Krupka, Peter,          ┆ Staudková, Hana            ┆ 792                 │
│ Medek, Jaroslav,        ┆ Petrůj, Svatopluk,         ┆ 761                 │
│ Frydryšková, Yvetta     ┆ Čechová, Jarmila           ┆ 730                 │
│ Hrdinová, Jarmila       ┆ Novák, František           ┆ 636                 │
│ Krupka, Peter,          ┆ Tůmová, Věra               ┆ 594                 │
│ Nechvátalová, Jana,     ┆ Tůmová, Věra               ┆ 594                 │
│ Kulík, Oldřich          ┆ Tláskal, Jaromír,          ┆ 583                 │
│ Nechvátalová, Jana,     ┆ Pišl, Milan,               ┆ 495                 │
│ Krupka, Peter,          ┆ Pišl, Milan,               ┆ 495                 │
│ Čupera, Jiří,           ┆ Ždánský, Bronislav         ┆ 468                 │
│ Nechvátalová, Jana,     ┆ Rektorys, Karel,           ┆ 462                 │
│ Krupka, Peter,          ┆ Rektorys, Karel,           ┆ 462                 │
│ Staudková, Hana         ┆ Tůmová, Věra               ┆ 438                 │
│ Jirák, Antonín,         ┆ Reitler, Antonín,          ┆ 390                 │
│ Lokay, Bohumil          ┆ Štolba, František          ┆ 387                 │
│ Pišl, Milan,            ┆ Staudková, Hana            ┆ 360                 │
│ Rektorys, Karel,        ┆ Staudková, Hana            ┆ 336                 │
│ Kubát, Jindřich         ┆ Ždánský, Bronislav         ┆ 315                 │
│ Hájek, Bohumil,         ┆ Otčenášek, Ladislav        ┆ 289                 │
│ Styblík, Vlastimil,     ┆ Šafránek, František        ┆ 272                 │
│ Pišl, Milan,            ┆ Tůmová, Věra               ┆ 270                 │
│ Doležalová, Alena Bára  ┆ Novák, František           ┆ 270                 │
│ Krsička, Rudolf         ┆ Ondráček, Josef            ┆ 256                 │
│ Chromá, Danuše          ┆ Münch, Otto                ┆ 255                 │
│ Rektorys, Karel,        ┆ Tůmová, Věra               ┆ 252                 │
│ Tožička, Bohumil,       ┆ Žofková, Lidmila,          ┆ 248                 │
│ Barborová, Lenka        ┆ Münch, Otto                ┆ 245                 │
│ Krupka, Peter,          ┆ Černá, Milada              ┆ 231                 │
│ Krupka, Peter,          ┆ Vřešťál, Evžen             ┆ 231                 │
│ Nechvátalová, Jana,     ┆ Vřešťál, Evžen             ┆ 231                 │
│ Nechvátalová, Jana,     ┆ Černá, Milada              ┆ 231                 │
│ Jelínková, Anna         ┆ Košťálová, Marie           ┆ 224                 │
│ Hechtová, Marie,        ┆ Košťálová, Marie           ┆ 224                 │
│ Hrdinová, Jarmila       ┆ Novotný, Miloš             ┆ 220                 │
│ Nykl, Jaroslav,         ┆ Rottová, Milada,           ┆ 216                 │
│ Chalupa, Petr,          ┆ Hübelová, Dana,            ┆ 212                 │
│ Červený, František,     ┆ Řehořovský, Václav Karel,  ┆ 211                 │
│ Pišl, Milan,            ┆ Rektorys, Karel,           ┆ 211                 │
│ Hampl, Rudolf,          ┆ Úl

In [47]:
df_autorske = df.filter(pl.col('700_4') == 'aut')

In [48]:
def hezkejmeno(sto):
    if not sto[-1].isalnum():
        sto = sto[:-1]
    if "," in sto:
        sto = sto.split(",")
        sto = sto[1].strip() + " " + sto[0].strip()
    return sto    

In [49]:
df_autorske = df_autorske.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jmeno1")).with_columns(pl.col("700_a").map_elements(hezkejmeno).alias("jmeno2"))

sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredict

In [50]:
df_autorske

shape: (164_250, 71)
┌──────────┬─────────────────┬────────────────┬────────────────┬───┬──────┬───────┬─────────────────┬────────────────┐
│ 100_ind1 ┆ 100_a           ┆ 100_7          ┆ 100_4          ┆ … ┆ rok  ┆ stran ┆ jmeno1          ┆ jmeno2         │
│ ---      ┆ ---             ┆ ---            ┆ ---            ┆   ┆ ---  ┆ ---   ┆ ---             ┆ ---            │
│ str      ┆ str             ┆ str            ┆ list[str]      ┆   ┆ i64  ┆ i64   ┆ str             ┆ str            │
╞══════════╪═════════════════╪════════════════╪════════════════╪═══╪══════╪═══════╪═════════════════╪════════════════╡
│ 1        ┆ Průchová,       ┆ jn19990209694  ┆ ["aut"]        ┆ … ┆ 2005 ┆ 229   ┆ Jarmila         ┆ Jaroslav       │
│          ┆ Jarmila,        ┆                ┆                ┆   ┆      ┆       ┆ Průchová        ┆ Průcha         │
│ 1        ┆ Kitz, Volker,   ┆ pna2012703405  ┆ ["aut"]        ┆ … ┆ 2012 ┆ 173   ┆ Volker Kitz     ┆ Manuel Tusch   │
│ 1        ┆ Štohl, Pavel,   ┆ xx0024514      ┆ ["aut"]        ┆ … ┆ 2009 ┆ 235   ┆ Pavel Štohl     ┆ Vladislav      │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Klička         │
│ 1        ┆ Kovařovič,      ┆ null           ┆ ["aut"]        ┆ … ┆ 1945 ┆ 4     ┆ Karel Kovařovič ┆ Karel Šípek    │
│          ┆ Karel           ┆                ┆                ┆   ┆      ┆       ┆                 ┆                │
│ 1        ┆ Jilík, Jiří,    ┆ jn20000401238  ┆ ["aut"]        ┆ … ┆ 2018 ┆ 231   ┆ Jiří Jilík      ┆ Bořek          │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Žižlavský      │
│ 1        ┆ Daněk, Wabi,    ┆ jn99240000151  ┆ ["aut"]        ┆ … ┆ 1984 ┆ 19    ┆ Wabi Daněk      ┆ Břetislav      │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Kotyza         │
│ 1        ┆ Daněk, Wabi,    ┆ jn99240000151  ┆ ["aut"]        ┆ … ┆ 1984 ┆ 19    ┆ Wabi Daněk      ┆ Karel Markytán │
│ 1        ┆ Brodská, Táňa,  ┆ js20071102002  ┆ ["aut"]        ┆ … ┆ 2023 ┆ 234   ┆ Táňa Brodská    ┆ Michelle       │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Losekoot       │
│ 1        ┆ Cejp, Martin,   ┆ jk01020589     ┆ ["aut"]        ┆ … ┆ 1980 ┆ 165   ┆ Martin Cejp     ┆ Milan Hromádka │
│ 1        ┆ Šustr, Milan    ┆ jx20101004025  ┆ ["aut", "pht"] ┆ … ┆ 2012 ┆ 45    ┆ Milan Šustr     ┆ Jaroslav Líbal │
│ 1        ┆ Majer, Jiří,    ┆ jk01073110     ┆ ["aut"]        ┆ … ┆ 1987 ┆ 45    ┆ Jiří Majer      ┆ Zdeněk Rasl    │
│ 1        ┆ Majer, Jiří,    ┆ jk01073110     ┆ ["aut"]        ┆ … ┆ 1987 ┆ 45    ┆ Jiří Majer      ┆ Karel Černý    │
│ 1        ┆ Kanda, Roman,   ┆ mzk2006356005  ┆ ["aut"]        ┆ … ┆ 2009 ┆ 183   ┆ Roman Kanda     ┆ Drahuše        │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Mašková        │
│ 1        ┆ Krajčovič,      ┆ mzk2004236874  ┆ ["aut"]        ┆ … ┆ 1998 ┆ 163   ┆ Marián          ┆ Petr Jůza      │
│          ┆ Marián,         ┆                ┆                ┆   ┆      ┆       ┆ Krajčovič       ┆                │
│ 1        ┆ Konůpková,      ┆ mzk2013757902  ┆ ["aut"]        ┆ … ┆ 2020 ┆ 1     ┆ Monika          ┆ Hana Marková   │
│          ┆ Monika          ┆                ┆                ┆   ┆      ┆       ┆ Konůpková       ┆                │
│ 1        ┆ Čákiová, Eva    ┆ null           ┆ ["aut"]        ┆ … ┆ 1991 ┆ 48    ┆ Eva Čákiová     ┆ Vladimír       │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Täubner        │
│ 1        ┆ Libnarová, Anna ┆ ola2004219925  ┆ ["aut"]        ┆ … ┆ 1999 ┆ 96    ┆ Anna Libnarová  ┆ Helena         │
│          ┆                 ┆                ┆                ┆   ┆      ┆       ┆                 ┆ Čornejová      │
│ 1        ┆ Bereczky,       ┆ null           ┆ ["au

In [51]:
def kombajmen(jmeno1, jmeno2, radit=True, spojeni = "a"):
    try:
        jmena = [jmeno1.split(" ")[-1], jmeno2.split(" ")[-1]]
        if radit == True:
            jmena.sort()
        return f" {spojeni} ".join(jmena)
    except Exception as e:
        print(e)
        return None

In [52]:
df_autorske = df_autorske.with_columns(pl.struct('jmeno1','jmeno2').map_elements(lambda x: kombajmen(x['jmeno1'], x['jmeno2'])).alias("dvojice"))

sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredict

In [53]:
df_autorske.group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (105_121, 2)
┌────────────────────────────┬───────┐
│ dvojice                    ┆ 245_a │
│ ---                        ┆ ---   │
│ str                        ┆ u32   │
╞════════════════════════════╪═══════╡
│ David a Soukup             ┆ 126   │
│ Nedbalová a Nedbalová      ┆ 90    │
│ Engels a Marx              ┆ 60    │
│ Benešová a Fukalová        ┆ 52    │
│ Benešová a Kanyzová        ┆ 52    │
│ Benešová a Šmíd            ┆ 52    │
│ Benešová a Formáčková      ┆ 52    │
│ Benešová a Příhoda         ┆ 52    │
│ Benešová a Vondrák         ┆ 52    │
│ Mihulová a Svoboda         ┆ 43    │
│ Brožová a Vostrá           ┆ 38    │
│ Nedbalcová a Zouharová     ┆ 36    │
│ Smíšek a Smíšková          ┆ 36    │
│ Voskovec a Werich          ┆ 35    │
│ Polášek a Polášková        ┆ 35    │
│ Jirotka a Vaněk            ┆ 34    │
│ Grimm a Grimm              ┆ 33    │
│ Kučera a Stach             ┆ 33    │
│ Child a Preston            ┆ 32    │
│ David a Dobrovolná         ┆ 31    │
│ Chmelař a Šimon            ┆ 29    │
│ Goscinny a Morris          ┆ 29    │
│ Klečka a Kunz              ┆ 28    │
│ Kubálek a Kubálková        ┆ 28    │
│ Kozák a Roček              ┆ 27    │
│ Hošková a Paprčka          ┆ 26    │
│ Lenin a Marx               ┆ 26    │
│ Jirotka a Turková          ┆ 26    │
│ Novák a Taterová           ┆ 25    │
│ Pešatová a Švingalová      ┆ 25    │
│ Augusta a Honzák           ┆ 25    │
│ Beran a Cílek              ┆ 25    │
│ Rusňáková a Sedláček       ┆ 25    │
│ Bartoňová a Vítková        ┆ 25    │
│ Bruthans a Kondrová        ┆ 24    │
│ Bruthans a Bůzek           ┆ 24    │
│ Pecinovský a Pecinovský    ┆ 24    │
│ Bruthans a Kadlecová       ┆ 23    │
│ Strugackij a Strugackij    ┆ 23    │
│ Erben a Němcová            ┆ 23    │
│ Jucovičová a Žáčková       ┆ 23    │
│ Mikulenková a Molnár       ┆ 22    │
│ Novák a Špička             ┆ 22    │
│ Beran a Jirotka            ┆ 22    │
│ Müller a Müllerová         ┆ 21    │
│ Novák a Nováková           ┆ 21    │
│ Bruthans a Kůrková         ┆ 21    │
│ Paetro a Patterson         ┆ 21    │
│ Bratršovská a Hrdlička     ┆ 21    │
│ Čadilová a Žampachová      ┆ 21    │
│ …                          ┆ …     │
│ Raclavská a Raclavský      ┆ 1     │
│ Jiránek a Taufer           ┆ 1     │
│ Mičín a Rešetka            ┆ 1     │
│ Pechová a Sadílková        ┆ 1     │
│ Doubravová a Kovalová      ┆ 1     │
│ Bukačová a Horyna          ┆ 1     │
│ Holmerová a Karen          ┆ 1     │
│ Květoňová a Němec          ┆ 1     │
│ Horváth a Marko            ┆ 1     │
│ Fleischmann a Livečka      ┆ 1     │
│ Oz a Roizen                ┆ 1     │
│ Abel a Soria               ┆ 1     │
│ Tempírová-Kotrlá a Turková ┆ 1     │
│ Brančíková a Knittlová     ┆ 1     │
│ Květoň a Pělucha           ┆ 1     │
│ Antonín a Křížová          ┆ 1     │
│ Konvalinka a Palán         ┆ 1     │
│ Jaroš a Veverka            ┆ 1     │
│ Baines a Málek             ┆ 1     │
│ Kaprálová a Přibáň         ┆ 1     │
│ Mašková a Trachtová        ┆ 1     │
│ Formánek a Veselý          ┆ 1     │
│ Capouchová a Štolcová      ┆ 1     │
│ Chlup a Horáček            ┆ 1     │
│ Musilová a Vaňura          ┆ 1     │
│ Hanson a Hanson            ┆ 1     │
│ Boudová a Pavlíková        ┆ 1     │
│ Horáček a Mrázová          ┆ 1     │
│ Komínek a Renner           ┆ 1     │
│ Měřička a Plášil           ┆ 1     │
│ Berger a Březina           ┆ 1     │
│ Blašková a Moll            ┆ 1     │
│ Bartoň a Knotková          ┆ 1     │
│ Bicanová a Galář           ┆ 1     │
│ Chvojka a Jiráň            ┆ 1     │
│ Cyrany a Kroupa            ┆ 1     │
│ Kašpar a Schiffner         ┆ 1     │
│ Cai a Hrabica              ┆ 1     │
│ Kovář a Simandl            ┆ 1     │
│ David a Rudloff            ┆ 1     │
│ Faltejsek a Vaňková        ┆ 1     │
│ Janovec a Landa            ┆ 1     │
│ Blažek a Mazanec           ┆ 1     │
│ Hanousek a Hořec           ┆ 1     │
│ Pistorius a Šalda          ┆ 1     │
│ Hůlka a Káně               ┆ 1     │
│ 

In [54]:
df_autorske.group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (111_219, 4)
┌────────────────────────────────┬────────────────┬──────────────────────────────┬───────┐
│ 100_a                          ┆ 100_7          ┆ 700_a                        ┆ 245_a │
│ ---                            ┆ ---            ┆ ---                          ┆ ---   │
│ str                            ┆ str            ┆ str                          ┆ u32   │
╞════════════════════════════════╪════════════════╪══════════════════════════════╪═══════╡
│ David, Petr,                   ┆ xx0006786      ┆ Soukup, Vladimír,            ┆ 126   │
│ Nedbalová, Marie               ┆ jo2014816080   ┆ Nedbalová, Josefína          ┆ 87    │
│ Marx, Karl,                    ┆ jn19990005454  ┆ Engels, Friedrich,           ┆ 59    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Kanyzová, Žofie,             ┆ 52    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Vondrák, Jan,                ┆ 52    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Fukalová, Lenka              ┆ 52    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Šmíd, Václav,                ┆ 52    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Formáčková, Marie,           ┆ 52    │
│ Benešová, Hana,                ┆ pna2012702164  ┆ Příhoda, Pavel,              ┆ 52    │
│ Mihulová, Marie,               ┆ jn20001227798  ┆ Svoboda, Milan               ┆ 43    │
│ Vostrá, Markéta                ┆ js20050801018  ┆ Brožová, Marie,              ┆ 38    │
│ Smíšek, Richard,               ┆ xx0038627      ┆ Smíšková, Kateřina,          ┆ 36    │
│ Smíšek, Richard,               ┆ xx0038627      ┆ Smíšková, Zuzana             ┆ 36    │
│ Nedbalcová, Kateřina           ┆ mzk2015871497  ┆ Zouharová, Monika            ┆ 33    │
│ Voskovec, Jiří,                ┆ jk01150746     ┆ Werich, Jan,                 ┆ 32    │
│ Preston, Douglas J.,           ┆ jn20000810185  ┆ Child, Lincoln,              ┆ 32    │
│ Grimm, Jacob Ludwig Karl,      ┆ jn19981228078  ┆ Grimm, Wilhelm Karl,         ┆ 32    │
│ David, Petr,                   ┆ xx0006786      ┆ Dobrovolná, Věra,            ┆ 30    │
│ Jirotka, Antonín,              ┆ jx20040623006  ┆ Vaněk, Jan J.,               ┆ 29    │
│ Morris,                        ┆ xx0038205      ┆ Goscinny, René,              ┆ 29    │
│ Klečka, Antonín,               ┆ jk01060331     ┆ Kunz, Emil,                  ┆ 28    │
│ Chmelař, František,            ┆ jk01050240     ┆ Šimon, Jaroslav,             ┆ 27    │
│ Paprčka, Milan,                ┆ osa2014838884  ┆ Hošková, Martina,            ┆ 26    │
│ Kozák, Jan,                    ┆ jk01062553     ┆ Roček, Jan,                  ┆ 26    │
│ Marx, Karl,                    ┆ jn19990005454  ┆ Lenin, Vladimir Il‘jič,      ┆ 26    │
│ Stach, Jan,                    ┆ jn20010309343  ┆ Kučera, Miroslav,            ┆ 26    │
│ Bartoňová, Miroslava,          ┆ mzk2004148531  ┆ Vítková, Marie,              ┆ 25    │
│ Polášková, Jiřina,             ┆ jn20000402028  ┆ Polášek, Jaromír,            ┆ 24    │
│ Augusta, Pavel,                ┆ jk01010424     ┆ Honzák, František,           ┆ 24    │
│ Bruthans, Jiří                 ┆ jx20090211004  ┆ Kondrová, Lucie,             ┆ 24    │
│ Bruthans, Jiří                 ┆ jx20090211004  ┆ Bůzek, František             ┆ 24    │
│ Taterová, Milada               ┆ jk01132074     ┆ Novák, Jiří,                 ┆ 23    │
│ Kubálek, Tomáš,                ┆ jo2002103223   ┆ Kubálková, Markéta,          ┆ 23    │
│ Strugackij, Arkadij Natanovič, ┆ jn19990210589  ┆ Strugackij, Boris Natanovič, ┆ 23    │
│ Jirotka, Antonín,              ┆ jx20040623006  ┆ Turková, Zoja,               ┆ 22    │
│ Bruthans, Jiří                 ┆ jx20090211004  ┆ Kadlecová, Renáta            ┆ 22    │
│ Nedbalcová, Kateřina           ┆ mzk2015871497  ┆ Matiašková, Katarína         ┆ 21    │
│ Bruthans, Jiří                 ┆ jx20090211004  ┆ Kůrková, Iva,                ┆ 21    │
│ Patterson, James,              ┆ jo20000076489  ┆ Paetro, Maxine,

In [55]:
df.filter(pl.col("700_a") == "Soukup, Vladimír,").filter(pl.col("100_a") == "David, Petr,")

shape: (197, 69)
┌──────────┬──────────────┬───────────┬────────────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a        ┆ 100_7     ┆ 100_4          ┆ … ┆ 700_5     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---          ┆ ---       ┆ ---            ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str          ┆ str       ┆ list[str]      ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪══════════════╪═══════════╪════════════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2016 ┆ 207   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1998 ┆ 159   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 95    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 376   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2007 ┆ 344   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 216   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2005 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2004 ┆ 224   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 157   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2013 ┆ 400   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 46    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2006 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2003 ┆ 161   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 95    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2005 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 87    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2006 ┆ 318   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 232   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1997 ┆ 56    │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2009 ┆ 384   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2006 ┆ 118   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2024 ┆ 365   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1993 ┆ 127   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 148   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2006 ┆ 190   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2011 ┆ 416   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 135   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut", "pht"] ┆ … ┆ null      ┆ null      ┆ 2015 ┆ 219   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2008 ┆ 464   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 308   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2002 ┆ 127   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut", "pht"] ┆ … ┆ null      ┆ null      ┆ 2020 ┆ 424   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2010 ┆ 199   │
│ 1        ┆ David, Petr, ┆ xx0006786 ┆ ["aut"]        ┆ … ┆ null      ┆ null      

## Ilustrátorstvo

In [57]:
df_ill = df.filter(pl.col('700_4') == 'ill')

In [58]:
df_ill = df_ill.with_columns(pl.col("100_a").map_elements(hezkejmeno).alias("jmeno1")).with_columns(pl.col("700_a").map_elements(hezkejmeno).alias("jmeno2"))

sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredict

In [59]:
df_ill = df_ill.with_columns(pl.struct('jmeno1','jmeno2').map_elements(lambda x: kombajmen(x['jmeno1'], x['jmeno2'], radit=False, spojeni="&")).alias("dvojice"))

sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredict

In [60]:
df_ill.filter(~pl.col("100_7").is_in(nechcemejetam)).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (32_227, 2)
┌─────────────────────────────────┬───────┐
│ dvojice                         ┆ 245_a │
│ ---                             ┆ ---   │
│ str                             ┆ u32   │
╞═════════════════════════════════╪═══════╡
│ Štíplová & Němeček              ┆ 108   │
│ Nedbalová & Popprová            ┆ 87    │
│ Nedbalová & Poppr               ┆ 68    │
│ Bass & Kratochvíl               ┆ 67    │
│ Švandrlík & Winter-Neprakta     ┆ 64    │
│ Čapek & Čapek                   ┆ 33    │
│ Pospíšilová & Trsťan            ┆ 31    │
│ Hašek & Lada                    ┆ 30    │
│ Rosecká & Růžička               ┆ 28    │
│ Škodová & Kubašta               ┆ 25    │
│ Pospíšilová & Vopičková         ┆ 25    │
│ Čtvrtek & Pilař                 ┆ 24    │
│ Foglar & Čermák                 ┆ 24    │
│ Tetourová & Plicková            ┆ 23    │
│ Piroddi & Baruzzi               ┆ 23    │
│ Macourek & Born                 ┆ 22    │
│ Drijverová & Otčenášek          ┆ 21    │
│ Žáček & Born                    ┆ 21    │
│ Válková & Kopl                  ┆ 21    │
│ Bednářová & Šmarda              ┆ 21    │
│ Šavlíková & Roverová            ┆ 20    │
│ Stará & Starý                   ┆ 19    │
│ Kratochvíl & Vydrová            ┆ 19    │
│ Walliams & Ross                 ┆ 19    │
│ Pospíšilová & Vydrová           ┆ 19    │
│ Steklač & Born                  ┆ 19    │
│ Grey & Hora                     ┆ 19    │
│ Webb & Williams                 ┆ 19    │
│ Wenig & Wenig                   ┆ 18    │
│ Hrubín & Trnka                  ┆ 18    │
│ Dahl & Blake                    ┆ 18    │
│ Potužníková & Jenčíková         ┆ 18    │
│ Hrušková & Turek                ┆ 18    │
│ Felix & Hísek                   ┆ 18    │
│ Brandt & Lefin                  ┆ 17    │
│ Voleská & Scheiner              ┆ 17    │
│ Pospíšilová & Sušina            ┆ 17    │
│ Štíplová & Vančurová            ┆ 17    │
│ Schovancová & Schovanec         ┆ 17    │
│ Brand & Wowk                    ┆ 17    │
│ Lebeda & Študlarová             ┆ 17    │
│ Osborne & Knipping              ┆ 16    │
│ Beigel & Goff                   ┆ 16    │
│ Johns & Barč                    ┆ 16    │
│ Simon & Ross                    ┆ 16    │
│ Běhounek & Junek                ┆ 16    │
│ Rožnovská & Vydrová             ┆ 16    │
│ Smolíková & Smolík              ┆ 16    │
│ Ciprová & Němcová               ┆ 16    │
│ Grey & Ulč                      ┆ 15    │
│ …                               ┆ …     │
│ O'Donnell & Miller              ┆ 1     │
│ Woodward & Bull                 ┆ 1     │
│ Brecht & Appen                  ┆ 1     │
│ Layman & Fabok                  ┆ 1     │
│ Tuláček & Kotrba                ┆ 1     │
│ Vančura & Erazim                ┆ 1     │
│ Stewart & Todd-Stanton          ┆ 1     │
│ Sampson & Phung                 ┆ 1     │
│ Nikitin & Mikulová              ┆ 1     │
│ Bobák & Laštuvková              ┆ 1     │
│ Vyskočil & Zmatlíková           ┆ 1     │
│ Layman & Booth                  ┆ 1     │
│ Řezáč & Brom                    ┆ 1     │
│ Philippe & Lhoták               ┆ 1     │
│ Novák & Offterdinger            ┆ 1     │
│ Chajda & Weishäupelová-Hockeov… ┆ 1     │
│ Szkandera & Janda               ┆ 1     │
│ Lustig & Vaca                   ┆ 1     │
│ Pečírka & Procházka             ┆ 1     │
│ Topsell & Malone                ┆ 1     │
│ Godefroy & Kubín                ┆ 1     │
│ Bednaříková & Vlasáková         ┆ 1     │
│ Svěrák & Otáhalová              ┆ 1     │
│ Dvořák & Suchardová             ┆ 1     │
│ Briquel & Place                 ┆ 1     │
│ Hanuš & Kropáček                ┆ 1     │
│ Judge & Judge                   ┆ 1     │
│ Šuleř & Severinová              ┆ 1     │
│ Kabeš & Lacina                  ┆ 1     │
│ Rue & Petersham                 ┆ 1     │
│ Červenka & Poláček              ┆ 1     │
│ Kocman & Bendová                ┆ 1     │
│ Hugo & Guth                     ┆ 1     │
│ Weltman & Milner                ┆ 1     │
│ Bičík & Spurný     

In [61]:
df_ill.filter(pl.col("dvojice") == "Vojkovský & Szcurek")

shape: (0, 72)
┌──────────┬───────┬───────┬───────────┬───┬───────┬────────┬────────┬─────────┐
│ 100_ind1 ┆ 100_a ┆ 100_7 ┆ 100_4     ┆ … ┆ stran ┆ jmeno1 ┆ jmeno2 ┆ dvojice │
│ ---      ┆ ---   ┆ ---   ┆ ---       ┆   ┆ ---   ┆ ---    ┆ ---    ┆ ---     │
│ str      ┆ str   ┆ str   ┆ list[str] ┆   ┆ i64   ┆ str    ┆ str    ┆ str     │
╞══════════╪═══════╪═══════╪═══════════╪═══╪═══════╪════════╪════════╪═════════╡
└──────────┴───────┴───────┴───────────┴───┴───────┴────────┴────────┴─────────┘

In [62]:
df_ill.filter(pl.col("dvojice") == "Štíplová & Němeček")

shape: (114, 72)
┌──────────┬───────────┬────────────┬───────────┬───┬───────┬────────────────┬──────────────────┬────────────┐
│ 100_ind1 ┆ 100_a     ┆ 100_7      ┆ 100_4     ┆ … ┆ stran ┆ jmeno1         ┆ jmeno2           ┆ dvojice    │
│ ---      ┆ ---       ┆ ---        ┆ ---       ┆   ┆ ---   ┆ ---            ┆ ---              ┆ ---        │
│ str      ┆ str       ┆ str        ┆ list[str] ┆   ┆ i64   ┆ str            ┆ str              ┆ str        │
╞══════════╪═══════════╪════════════╪═══════════╪═══╪═══════╪════════════════╪══════════════════╪════════════╡
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 160   ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 143   ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 66    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 163   ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ Štíplová & │
│          ┆ Ljuba,    ┆            ┆           ┆   ┆       ┆                ┆                  ┆ Němeček    │
│ 1        ┆ Štíplová, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ 34    ┆ Ljuba Štíplová ┆ Jaroslav Němeček ┆ 

In [63]:
df_ill.filter(pl.col("dvojice") == "Nedbalová & Popprová")

shape: (188, 72)
┌──────────┬────────────┬──────────────┬───────────┬───┬───────┬───────────────────┬───────────────────┬─────────────┐
│ 100_ind1 ┆ 100_a      ┆ 100_7        ┆ 100_4     ┆ … ┆ stran ┆ jmeno1            ┆ jmeno2            ┆ dvojice     │
│ ---      ┆ ---        ┆ ---          ┆ ---       ┆   ┆ ---   ┆ ---               ┆ ---               ┆ ---         │
│ str      ┆ str        ┆ str          ┆ list[str] ┆   ┆ i64   ┆ str               ┆ str               ┆ str         │
╞══════════╪════════════╪══════════════╪═══════════╪═══╪═══════╪═══════════════════╪═══════════════════╪═════════════╡
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Andrea Popprová   ┆ Nedbalová & │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆                   ┆ Popprová    │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆

In [64]:
df_ill.filter(pl.col("dvojice") == "Burroughs & Pešek")

shape: (23, 72)
┌──────────┬──────────────────┬───────────────┬───────────┬───┬───────┬────────────┬───────────────┬─────────────┐
│ 100_ind1 ┆ 100_a            ┆ 100_7         ┆ 100_4     ┆ … ┆ stran ┆ jmeno1     ┆ jmeno2        ┆ dvojice     │
│ ---      ┆ ---              ┆ ---           ┆ ---       ┆   ┆ ---   ┆ ---        ┆ ---           ┆ ---         │
│ str      ┆ str              ┆ str           ┆ list[str] ┆   ┆ i64   ┆ str        ┆ str           ┆ str         │
╞══════════╪══════════════════╪═══════════════╪═══════════╪═══╪═══════╪════════════╪═══════════════╪═════════════╡
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 134   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 142   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 140   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 126   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 123   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 177   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 156   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 153   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 188   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 124   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 165   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 181   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 127   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 124   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Burroughs  ┆               ┆ Pešek       │
│ 1        ┆ Burroughs, Edgar ┆ jn19990001239 ┆ ["aut"]   ┆ … ┆ 182   ┆ Edgar Rice ┆ Richard Pešek ┆ Burroughs & │
│          ┆ Rice,            ┆               ┆           ┆   ┆       ┆ Bu

In [65]:
df_ill.filter(pl.col("dvojice") == "Nedbalová & Poppr")

shape: (72, 72)
┌──────────┬────────────┬──────────────┬───────────┬───┬───────┬───────────────────┬─────────────┬───────────────────┐
│ 100_ind1 ┆ 100_a      ┆ 100_7        ┆ 100_4     ┆ … ┆ stran ┆ jmeno1            ┆ jmeno2      ┆ dvojice           │
│ ---      ┆ ---        ┆ ---          ┆ ---       ┆   ┆ ---   ┆ ---               ┆ ---         ┆ ---               │
│ str      ┆ str        ┆ str          ┆ list[str] ┆   ┆ i64   ┆ str               ┆ str         ┆ str               │
╞══════════╪════════════╪══════════════╪═══════════╪═══╪═══════╪═══════════════════╪═════════════╪═══════════════════╡
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 6     ┆ Marie Nedbalová   ┆ Roman Poppr ┆ Nedbalová & Poppr │
│          ┆ Marie      ┆              ┆           ┆   ┆       ┆                   ┆             ┆                   │
│ 1        ┆ Nedbalová, ┆ jo2014816080 ┆ ["aut"]   ┆ … ┆ 

In [66]:
dvojice_aut_ill = df_ill.filter(~pl.col("100_7").is_in(nechcemejetam)).filter(pl.col("stran") > 30).group_by(['dvojice']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True).head(10).select(pl.col("dvojice")).to_series().to_list()
dvojice_aut_ill

['Štíplová & Němeček',
 'Švandrlík & Winter-Neprakta',
 'Hašek & Lada',
 'Pospíšilová & Trsťan',
 'Čapek & Čapek',
 'Rosecká & Růžička',
 'Foglar & Čermák',
 'Macourek & Born',
 'Válková & Kopl',
 'Drijverová & Otčenášek']

In [83]:
import datetime

In [84]:
do_grafu = df_ill.filter(pl.col("dvojice").is_in(dvojice_aut_ill)).with_columns(pl.col("rok").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))

In [85]:
import altair as alt

In [86]:
def irozhlas_conf():

    return {
        "config" : {
             "title": {'font': "Noticia Text",
                      'fontSize': 14,
                      'anchor': 'start',
                       'fontWeight': 'bolder',
                    'subtitleFont': 'Noticia Text',
                      'subtitleFontSize': 12,
                       'subtitleFontWeight': 'lighter',
                      'subtitlePadding': 12,
                       'dy': -12,
                      },
             "axis": {
                "labelFont": "Asap",
                "titleFont": "Asap",
                 "fontWeight": "lighter",
                "titleFontWeight": "lighter",
                "labelFontSize": 10,
                "titleFontSize": 10,
                'labelPadding': 2,
                 'titlePadding': 10
            },
            "legend": {
                "labelFont": "Asap",
                "labelFontWeight": "normal",
                "titleFont": "Asap",
                "titleFontWeight": "normal",
                "labelFontSize": 10,
                "titleFontSize": 10
            }
        }
    }

alt.themes.register('irozhlas', irozhlas_conf)
alt.themes.enable('irozhlas')

ThemeRegistry.enable('irozhlas')

In [87]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [88]:
zebricek = alt.Chart(do_grafu.to_pandas(), title=alt.TitleParams(f"{len(dvojice_aut_ill)} nejčastějších dvojic psali-ilustrovali (bez reprintů)"), width=300).mark_circle(size=8) \
        .encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')), 
            y=alt.Y("dvojice:N", sort=dvojice_aut_ill, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='#DCDDD6')), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('dvojice:N', scale=alt.Scale(range=['#D6534B', '#445B78', '#DB842F', '#70871E']), 
                            sort=dvojice_aut_ill).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())").configure_view(stroke='transparent')

zebricek

C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.

alt.Chart(...)

In [89]:
df_ill.group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (34_426, 4)
┌─────────────────────────────────┬────────────────┬────────────────────────┬───────┐
│ 100_a                           ┆ 100_7          ┆ 700_a                  ┆ 245_a │
│ ---                             ┆ ---            ┆ ---                    ┆ ---   │
│ str                             ┆ str            ┆ str                    ┆ u32   │
╞═════════════════════════════════╪════════════════╪════════════════════════╪═══════╡
│ Štíplová, Ljuba,                ┆ jk01131441     ┆ Němeček, Jaroslav,     ┆ 108   │
│ Nedbalová, Marie                ┆ jo2014816080   ┆ Popprová, Andrea       ┆ 87    │
│ Nedbalová, Marie                ┆ jo2014816080   ┆ Poppr, Roman           ┆ 68    │
│ Bass, Eduard,                   ┆ jk01011066     ┆ Kratochvíl, Zdeněk,    ┆ 67    │
│ Švandrlík, Miloslav,            ┆ jk01131832     ┆ Winter-Neprakta, Jiří, ┆ 64    │
│ Wilson, Jacqueline,             ┆ jn20010310318  ┆ Sharratt, Nick,        ┆ 52    │
│ Delahaye, Gilbert,              ┆ xx0203193      ┆ Marlier, Marcel,       ┆ 51    │
│ Verne, Jules,                   ┆ jn19990008769  ┆ Benett, Léon,          ┆ 50    │
│ Brezina, Thomas,                ┆ jn20001227589  ┆ Fearn, Naomi,          ┆ 43    │
│ Verne, Jules,                   ┆ jn19990008769  ┆ Roux, George,          ┆ 42    │
│ Goscinny, René,                 ┆ jn20000602144  ┆ Uderzo, Albert,        ┆ 42    │
│ Deary, Terry,                   ┆ jn20001103401  ┆ Brown, Martin,         ┆ 36    │
│ Arnold, Nick,                   ┆ xx0008006      ┆ De Saulles, Tony       ┆ 33    │
│ Čapek, Karel,                   ┆ jk01021023     ┆ Čapek, Josef,          ┆ 33    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486  ┆ Trsťan, Drahomír,      ┆ 31    │
│ Meadows, Daisy                  ┆ xx0082647      ┆ Ripper, Georgie,       ┆ 29    │
│ Hašek, Jaroslav,                ┆ jk01040097     ┆ Lada, Josef,           ┆ 29    │
│ Rosecká, Zdena                  ┆ jx20031130107  ┆ Růžička, Jiří          ┆ 28    │
│ Škodová, Helena,                ┆ jx20040618039  ┆ Kubašta, Vojtěch,      ┆ 25    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486  ┆ Vopičková, Vladimíra   ┆ 25    │
│ Awdry, W.,                      ┆ xx0010566      ┆ Davies, Robin,         ┆ 24    │
│ Čtvrtek, Václav,                ┆ jk01021929     ┆ Pilař, Radek,          ┆ 24    │
│ Tetourová, Marie,               ┆ jn20001005512  ┆ Plicková, Edita,       ┆ 23    │
│ Burroughs, Edgar Rice,          ┆ jn19990001239  ┆ Pešek, Richard,        ┆ 23    │
│ Awdry, W.,                      ┆ xx0010566      ┆ Smith, Jerry           ┆ 23    │
│ Piroddi, Chiara,                ┆ osa2017965599  ┆ Baruzzi, Agnese,       ┆ 23    │
│ Foglar, Jaroslav,               ┆ jk01031485     ┆ Čermák, Marko,         ┆ 22    │
│ Macourek, Miloš,                ┆ jk01072813     ┆ Born, Adolf,           ┆ 22    │
│ Žáček, Jiří,                    ┆ jk01152946     ┆ Born, Adolf,           ┆ 21    │
│ Drijverová, Martina,            ┆ jk01023067     ┆ Otčenášek, Vojtěch,    ┆ 21    │
│ May, Karl,                      ┆ jn19990005499  ┆ Krum, Gustav,          ┆ 21    │
│ Válková, Veronika,              ┆ jo2005274171   ┆ Kopl, Petr,            ┆ 21    │
│ Bednářová, Jiřina,              ┆ mzk2004248919  ┆ Šmarda, Richard,       ┆ 21    │
│ Šavlíková, Lucie,               ┆ jn19981002458  ┆ Roverová, Eva          ┆ 20    │
│ May, Karl,                      ┆ jn19990005499  ┆ Ulrich, Josef,         ┆ 19    │
│ Webb, Holly                     ┆ ola2010577122  ┆ Williams, Sophy        ┆ 19    │
│ Kratochvíl, Miloš,              ┆ jk01062996     ┆ Vydrová, Markéta,      ┆ 19    │
│ Stará, Ester,                   ┆ mzk2004261153  ┆ Starý, Milan,          ┆ 19    │
│ Pospíšilová, Zuzana,            ┆ mzk2006331486  ┆ Vydrová, Markéta,      ┆ 19    │
│ Walliams, David,                ┆ xx0158956      ┆ Ross, Tony,            ┆ 19    │
│ Steklač, Vojtěch,               ┆ jk01121138     ┆ Born, Adolf,           ┆ 19    │
│ Grey, Zane,            

In [90]:
ctyrlistek_leader = " <leader>     cam a22      a 4500"
ctyrlistek_leader = ctyrlistek_leader.split(">")[1]
print(ctyrlistek_leader[6])
print(ctyrlistek_leader[7])

a
m


In [91]:
df.filter(pl.col("100_a") == "Štíplová, Ljuba,").filter(pl.col("700_a") == "Němeček, Jaroslav,"	).sort(by="rok")

shape: (116, 69)
┌──────────┬──────────────────┬────────────┬───────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a            ┆ 100_7      ┆ 100_4     ┆ … ┆ 700_5     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---              ┆ ---        ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str              ┆ str        ┆ list[str] ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪══════════════════╪════════════╪═══════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1972 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1973 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 35    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 11    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 50    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1976 ┆ 11    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      ┆ 1977 ┆ 34    │
│ 1        ┆ Štíplová, Ljuba, ┆ jk01131441 ┆ ["aut"]   ┆ … ┆ null      ┆ null      

In [92]:
df.filter(pl.col('700_4') == 'ill').filter(~pl.col("100_7").is_in(nechcemejetam)).group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True).rename({'100_a':'autor/ka','700_a':'ilustrátor/ka','245_a':'společných knih'}).drop("100_7")

shape: (32_537, 3)
┌─────────────────────────────────┬─────────────────────────────┬─────────────────┐
│ autor/ka                        ┆ ilustrátor/ka               ┆ společných knih │
│ ---                             ┆ ---                         ┆ ---             │
│ str                             ┆ str                         ┆ u32             │
╞═════════════════════════════════╪═════════════════════════════╪═════════════════╡
│ Štíplová, Ljuba,                ┆ Němeček, Jaroslav,          ┆ 108             │
│ Nedbalová, Marie                ┆ Popprová, Andrea            ┆ 87              │
│ Nedbalová, Marie                ┆ Poppr, Roman                ┆ 68              │
│ Bass, Eduard,                   ┆ Kratochvíl, Zdeněk,         ┆ 67              │
│ Švandrlík, Miloslav,            ┆ Winter-Neprakta, Jiří,      ┆ 64              │
│ Čapek, Karel,                   ┆ Čapek, Josef,               ┆ 33              │
│ Pospíšilová, Zuzana,            ┆ Trsťan, Drahomír,           ┆ 31              │
│ Hašek, Jaroslav,                ┆ Lada, Josef,                ┆ 29              │
│ Rosecká, Zdena                  ┆ Růžička, Jiří               ┆ 28              │
│ Škodová, Helena,                ┆ Kubašta, Vojtěch,           ┆ 25              │
│ Pospíšilová, Zuzana,            ┆ Vopičková, Vladimíra        ┆ 25              │
│ Čtvrtek, Václav,                ┆ Pilař, Radek,               ┆ 24              │
│ Piroddi, Chiara,                ┆ Baruzzi, Agnese,            ┆ 23              │
│ Tetourová, Marie,               ┆ Plicková, Edita,            ┆ 23              │
│ Foglar, Jaroslav,               ┆ Čermák, Marko,              ┆ 22              │
│ Macourek, Miloš,                ┆ Born, Adolf,                ┆ 22              │
│ Žáček, Jiří,                    ┆ Born, Adolf,                ┆ 21              │
│ Drijverová, Martina,            ┆ Otčenášek, Vojtěch,         ┆ 21              │
│ Válková, Veronika,              ┆ Kopl, Petr,                 ┆ 21              │
│ Bednářová, Jiřina,              ┆ Šmarda, Richard,            ┆ 21              │
│ Šavlíková, Lucie,               ┆ Roverová, Eva               ┆ 20              │
│ Kratochvíl, Miloš,              ┆ Vydrová, Markéta,           ┆ 19              │
│ Stará, Ester,                   ┆ Starý, Milan,               ┆ 19              │
│ Pospíšilová, Zuzana,            ┆ Vydrová, Markéta,           ┆ 19              │
│ Steklač, Vojtěch,               ┆ Born, Adolf,                ┆ 19              │
│ Grey, Zane,                     ┆ Hora, Jan,                  ┆ 19              │
│ Webb, Holly                     ┆ Williams, Sophy             ┆ 19              │
│ Walliams, David,                ┆ Ross, Tony,                 ┆ 19              │
│ Potužníková, Ema                ┆ Jenčíková, Lucie            ┆ 18              │
│ Hrubín, František,              ┆ Trnka, Jiří,                ┆ 18              │
│ Felix, Jiří,                    ┆ Hísek, Květoslav,           ┆ 18              │
│ Dahl, Roald,                    ┆ Blake, Quentin,             ┆ 18              │
│ Hrušková, Marie,                ┆ Turek, Jaroslav,            ┆ 18              │
│ Pospíšilová, Zuzana,            ┆ Sušina, Michal              ┆ 17              │
│ Lebeda, Jan,                    ┆ Študlarová, Zdeňka,         ┆ 17              │
│ Brand, Max,                     ┆ Wowk, Jiří,                 ┆ 17              │
│ Brandt, Susanne,                ┆ Lefin, Petra,               ┆ 17              │
│ Voleská, Marta,                 ┆ Scheiner, Artuš,            ┆ 17              │
│ Schovancová, Běla,              ┆ Schovanec, Ladislav,        ┆ 17              │
│ Štíplová, Ljuba,                ┆ Janoušková Vančurová, Alena ┆ 17              │
│ Johns, William Earl,            ┆ Barč, Petr,                 ┆ 16              │
│ Ciprová, Oldřiška,              ┆ Němcová, Lenka,             ┆ 16              │
│ Beigel, Christine,             

In [93]:
df.filter(pl.col('700_4') == 'trl').group_by(['100_a','100_7','700_a']).agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (66_285, 4)
┌─────────────────────────────┬───────────────────┬────────────────────────────┬───────┐
│ 100_a                       ┆ 100_7             ┆ 700_a                      ┆ 245_a │
│ ---                         ┆ ---               ┆ ---                        ┆ ---   │
│ str                         ┆ str               ┆ str                        ┆ u32   │
╞═════════════════════════════╪═══════════════════╪════════════════════════════╪═══════╡
│ Unger, Gert F.,             ┆ jn20001103529     ┆ Butala, Tomáš,             ┆ 311   │
│ Kirby, John                 ┆ jx20040611003     ┆ Pavka, Marek,              ┆ 182   │
│ Courths-Mahler, Hedwig,     ┆ jn19990001513     ┆ Schönová, Zuzana           ┆ 120   │
│ Scott, William,             ┆ ola2003188680     ┆ Butala, Tomáš,             ┆ 101   │
│ Birkner-Mahler, Frieda,     ┆ jn20000600873     ┆ Lacinová, Libuše,          ┆ 80    │
│ Unger, Gert F.,             ┆ jn20001103529     ┆ Schönová, Zuzana           ┆ 80    │
│ Unger, Gert F.,             ┆ jn20001103529     ┆ Sedláčková, Libuše         ┆ 77    │
│ Pratchett, Terry,           ┆ jo20000080627     ┆ Kantůrek, Jan,             ┆ 57    │
│ Brezina, Thomas,            ┆ jn20001227589     ┆ Steidlová, Dagmar,         ┆ 55    │
│ Courths-Mahler, Hedwig,     ┆ jn19990001513     ┆ Lacinová, Libuše,          ┆ 54    │
│ Lane, Lex                   ┆ ola2007364818     ┆ Pavka, Marek,              ┆ 53    │
│ Dark, Jason,                ┆ jn20000810032     ┆ Sychra, Pavel              ┆ 50    │
│ Nieritz, Gustav,            ┆ jo20000080760     ┆ Tomsa, František Bohumil,  ┆ 49    │
│ Dark, Jason,                ┆ jn20000810032     ┆ Küchler, Marek             ┆ 48    │
│ Unger, Gert F.,             ┆ jn20001103529     ┆ Sychra, Pavel              ┆ 48    │
│ Hayes, Rex,                 ┆ jn20020717154     ┆ Pavka, Marek,              ┆ 46    │
│ Shakespeare, William,       ┆ jn19981002129     ┆ Sládek, Josef Václav,      ┆ 46    │
│ Etzold, Hans-Rüdiger,       ┆ xx0020263         ┆ Hlásek, Pavel              ┆ 45    │
│ Steiner, Rudolf,            ┆ jn19990009728     ┆ Hradil, Radomil,           ┆ 44    │
│ Francis, Dick,              ┆ jn19990002376     ┆ Moserová, Jaroslava,       ┆ 43    │
│ Wallace, Edgar,             ┆ jn19990008883     ┆ Heller, František          ┆ 43    │
│ Davis, Jim,                 ┆ jn20010601536     ┆ Škába, Filip,              ┆ 42    │
│ Shakespeare, William,       ┆ jn19981002129     ┆ Hilský, Martin,            ┆ 42    │
│ Mark, William,              ┆ jo20241218643     ┆ Kuťák, Jaroslav,           ┆ 42    │
│ Velden, Irene von           ┆ jx20031204026     ┆ Chromiaková, Eva           ┆ 40    │
│ May, Karl,                  ┆ jn19990005499     ┆ Šunda, Vladimír            ┆ 39    │
│ Wilson, Jacqueline,         ┆ jn20010310318     ┆ Feltová, Daniela,          ┆ 38    │
│ Unger, Gert F.,             ┆ jn20001103529     ┆ Veselý, Milan              ┆ 37    │
│ Verne, Jules,               ┆ jn19990008769     ┆ Unzeitig, Vítězslav,       ┆ 36    │
│ Dark, Jason,                ┆ jn20000810032     ┆ Brzobohatý, Rostislav      ┆ 35    │
│ Patterson, James,           ┆ jo20000076489     ┆ Duha, Ondřej               ┆ 35    │
│ Wild, Dunja                 ┆ ola20040510003    ┆ Smolaková, Helena          ┆ 35    │
│ Cartland, Barbara,          ┆ jn19990001350     ┆ Volná, Kristina,           ┆ 34    │
│ Andrée, Michaela            ┆ ola2003188685     ┆ Smolaková, Helena          ┆ 34    │
│ Platón,                     ┆ jn19981001996     ┆ Novotný, František,        ┆ 33    │
│ McBain, Ed,                 ┆ jn19981001834     ┆ Maxová, Alena,             ┆ 33    │
│ King, Stephen,              ┆ jn19990004346     ┆ Bartošková, Linda,         ┆ 32    │
│ Ošó,                        ┆ jn19981001926     ┆ Žlábková, Jana,            ┆ 32    │
│ Vandenberg, Patricia,       ┆ jn20000810141     ┆ Všetulová, Marisa          ┆ 31    │
│ Deaver, Jeffery,            ┆ jn20001103550     ┆ Kobělka, Jiří

In [94]:
df.filter(pl.col('700_4') == 'ill').group_by('700_a').agg(pl.col("100_a").n_unique()).sort(by="100_a",descending=True)

shape: (13_633, 2)
┌─────────────────────────────────┬───────┐
│ 700_a                           ┆ 100_a │
│ ---                             ┆ ---   │
│ str                             ┆ u32   │
╞═════════════════════════════════╪═══════╡
│ Born, Adolf,                    ┆ 149   │
│ Burian, Zdeněk,                 ┆ 112   │
│ Bouda, Cyril,                   ┆ 112   │
│ Krejčová, Zdeňka,               ┆ 98    │
│ Svolinský, Karel,               ┆ 93    │
│ Zmatlíková, Helena,             ┆ 80    │
│ Aleš, Mikoláš,                  ┆ 80    │
│ Petráček, Jiří,                 ┆ 78    │
│ Jiránek, Vladimír,              ┆ 75    │
│ Šplíchal, Antonín,              ┆ 73    │
│ Slíva, Jiří,                    ┆ 73    │
│ Černý, Věnceslav,               ┆ 69    │
│ Plicková, Edita,                ┆ 67    │
│ Čuma, Aleš,                     ┆ 67    │
│ Thuma, Karel Ladislav,          ┆ 67    │
│ Teissig, Karel,                 ┆ 65    │
│ Procházka, Otakar               ┆ 65    │
│ Winter-Neprakta, Jiří,          ┆ 65    │
│ Lada, Josef,                    ┆ 62    │
│ Lhoták, Kamil,                  ┆ 61    │
│ Komárek, Vladimír,              ┆ 61    │
│ Urban, Petr,                    ┆ 60    │
│ Janeček, Ota,                   ┆ 60    │
│ Martenek, Miloslav,             ┆ 58    │
│ Kabát, Václav,                  ┆ 55    │
│ Černý, Jan,                     ┆ 55    │
│ Fixl, Jiří,                     ┆ 55    │
│ Tesař, Vladimír,                ┆ 53    │
│ Netopil, Zdeněk,                ┆ 53    │
│ Velčovský, Josef,               ┆ 53    │
│ Jakešová, Miroslava,            ┆ 52    │
│ Čutta, Václav,                  ┆ 52    │
│ Škoda, František,               ┆ 51    │
│ Duda, Stanislav,                ┆ 50    │
│ Renčín, Vladimír,               ┆ 49    │
│ Trnka, Jiří,                    ┆ 49    │
│ Čechová, Olga,                  ┆ 48    │
│ Kalousek, Jiří,                 ┆ 48    │
│ Váša, Miroslav,                 ┆ 46    │
│ Scheiner, Artuš,                ┆ 45    │
│ Barták, Miroslav,               ┆ 45    │
│ Kovařík, Jindřich,              ┆ 44    │
│ Zpěvák, Karel                   ┆ 44    │
│ Nesvadba, Miloš,                ┆ 44    │
│ Jágr, Miloslav,                 ┆ 43    │
│ Konůpek, Jan,                   ┆ 43    │
│ Anlauf, Lubomír,                ┆ 42    │
│ Franta, Karel,                  ┆ 42    │
│ Drobný, Libor,                  ┆ 42    │
│ Mézl, Zdeněk,                   ┆ 41    │
│ …                               ┆ …     │
│ Foltová, Vladimíra              ┆ 1     │
│ Vondrová, Veronika              ┆ 1     │
│ Hansson, Gunilla,               ┆ 1     │
│ Adamcová, Jarmila               ┆ 1     │
│ Suski, Tadeusz                  ┆ 1     │
│ Witschonke, Alan,               ┆ 1     │
│ Jayakrishnan, K. P.             ┆ 1     │
│ Smejkalová, Hana                ┆ 1     │
│ Souppart, Gaëlle                ┆ 1     │
│ Billerová, Taťána               ┆ 1     │
│ Dunděra, Jiří,                  ┆ 1     │
│ Korityák, Stanislav,            ┆ 1     │
│ Martin, Caroline                ┆ 1     │
│ Fornari, Giuliano               ┆ 1     │
│ Ermos, George                   ┆ 1     │
│ Holomý, Zdeněk,                 ┆ 1     │
│ Joska, Luděk                    ┆ 1     │
│ Caruso, Sergio                  ┆ 1     │
│ Levý, Josef                     ┆ 1     │
│ Treuchel, Josef,                ┆ 1     │
│ Ivojlova, Aleksandra Valer‘jev… ┆ 1     │
│ Bohnstedt, Antje,               ┆ 1     │
│ Nikodým, Milan                  ┆ 1     │
│ Rytter Jensen, Dagmar,          ┆ 1     │
│ Levey, Emma                     ┆ 1     │
│ Fricker, Steve,                 ┆ 1     │
│ Křečková, Alžběta               ┆ 1     │
│ Goto, Keisuke                   ┆ 1     │
│ Roeselová, Věra                 ┆ 1     │
│ Martínek, Jan                   ┆ 1     │
│ De Pieri, Erika,                ┆ 1     │
│ Čapka, Marián,                  ┆ 1     │
│ Tockstein, Jindřich,            ┆ 1     │
│ Krhin, Kristina,                ┆ 1     │
│ Geudens, Tony,     

In [95]:
nejaktivnejsi_ilustratori = df.filter(pl.col("stran") > 30).filter(pl.col('700_4') == 'ill').group_by('700_a').agg(pl.struct(["100_a","245_a"]).n_unique()).sort(by="100_a",descending=True).head(10).select(pl.col("700_a")).to_series().to_list()
nejaktivnejsi_ilustratori

['Born, Adolf,',
 'Burian, Zdeněk,',
 'Winter-Neprakta, Jiří,',
 'Němeček, Jaroslav,',
 'Krejčová, Zdeňka,',
 'Bouda, Cyril,',
 'Zmatlíková, Helena,',
 'Černý, Věnceslav,',
 'Thuma, Karel Ladislav,',
 'Šplíchal, Antonín,']

In [96]:
def hezkejmeno(sto):
    if not sto[-1].isalnum():
        sto = sto[:-1]
    if "," in sto:
        sto = sto.split(",")
        sto = sto[1].strip() + " " + sto[0].strip()
    return sto    

In [97]:
do_grafu2 = df.filter(pl.col('700_a').is_in(nejaktivnejsi_ilustratori)).with_columns(pl.col('700_a').map_elements(hezkejmeno)).with_columns(pl.col("rok").map_elements(lambda x: datetime.date(year=int(x), month=1, day=1), return_dtype=pl.Date).cast(pl.Datetime))
nejaktivnejsi_ilustratori2 = do_grafu2.group_by('700_a').agg(pl.struct(["100_a","245_a"]).n_unique()).sort(by="100_a",descending=True).head(10).select(pl.col("700_a")).to_series().to_list()

sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredictable results. Specify `return_dtype` to silence this warning.
sys:1: MapWithoutReturnDtypeWarning: Calling `map_elements` without specifying `return_dtype` can lead to unpredict

In [98]:
zebricek2 = alt.Chart(do_grafu2.to_pandas(), title=alt.TitleParams(f"{len(dvojice_aut_ill)} nejčastějších dvojic psali-ilustrovali (bez reprintů)"), width=300).mark_circle(size=8) \
        .encode(
            x=alt.X("rok:T", title=None, axis=alt.Axis(domainOpacity=0, tickColor='#DCDDD6')), 
            y=alt.Y("700_a:N", sort=nejaktivnejsi_ilustratori2, title=None, axis=alt.Axis(orient='left', domainOpacity=0, tickColor='#DCDDD6')), 
            yOffset=alt.YOffset("jitter:Q", scale=alt.Scale(range=[3, 15])), 
            color=alt.Color('700_a:N', scale=alt.Scale(range=['#D6534B', '#445B78', '#DB842F', '#70871E']), 
                            sort=nejaktivnejsi_ilustratori2).legend(None)) \
        .transform_calculate(jitter="sqrt(-2*log(random()))*cos(2*PI*random())").configure_view(stroke='transparent')

zebricek2

C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.py:395: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
C:\Users\micha\anaconda3\Lib\site-packages\altair\utils\core.

alt.Chart(...)

In [99]:
df.filter(pl.col('700_a') == 'Born, Adolf,')

shape: (443, 69)
┌──────────┬─────────────────────────────┬───────────────┬────────────────┬───┬───────────┬───────────┬──────┬───────┐
│ 100_ind1 ┆ 100_a                       ┆ 100_7         ┆ 100_4          ┆ … ┆ 700_5     ┆ 700_g     ┆ rok  ┆ stran │
│ ---      ┆ ---                         ┆ ---           ┆ ---            ┆   ┆ ---       ┆ ---       ┆ ---  ┆ ---   │
│ str      ┆ str                         ┆ str           ┆ list[str]      ┆   ┆ list[str] ┆ list[str] ┆ i64  ┆ i64   │
╞══════════╪═════════════════════════════╪═══════════════╪════════════════╪═══╪═══════════╪═══════════╪══════╪═══════╡
│ 1        ┆ Kortooms, Toon,             ┆ ola2003191710 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1978 ┆ 206   │
│ 1        ┆ Adlová, Věra,               ┆ jk01010127    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1983 ┆ 125   │
│ 1        ┆ Defoe, Daniel,              ┆ jn19990001679 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 508   │
│ 1        ┆ Nepil, František,           ┆ jk01083177    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2014 ┆ 92    │
│ 1        ┆ Drijverová, Martina,        ┆ jk01023067    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2021 ┆ 62    │
│ 1        ┆ Holcová, Milena,            ┆ jn99240000298 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2001 ┆ 195   │
│ 1        ┆ Žáček, Jiří,                ┆ jk01152946    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2011 ┆ 303   │
│ 1        ┆ Žáček, Jiří,                ┆ jk01152946    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2007 ┆ 75    │
│ 1        ┆ Steklač, Vojtěch,           ┆ jk01121138    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2022 ┆ 185   │
│ 1        ┆ Durrell, Gerald Malcolm,    ┆ jn19981000804 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1986 ┆ 340   │
│ 1        ┆ Hercíková, Iva,             ┆ jk01040797    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1993 ┆ 101   │
│ 1        ┆ Hrušínská, Eva,             ┆ jn20000401098 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2000 ┆ 115   │
│ 1        ┆ Dumas, Alexandre,           ┆ jn19990001907 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2016 ┆ 3     │
│ 1        ┆ Pavel, Ota,                 ┆ jk01092027    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1981 ┆ 267   │
│ 1        ┆ Říha, Bohumil,              ┆ jk01110164    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1982 ┆ 264   │
│ 1        ┆ Svěrák, Zdeněk,             ┆ jk01121890    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2022 ┆ 45    │
│ 1        ┆ Pavel, Ota,                 ┆ jk01092027    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1974 ┆ 46    │
│ 1        ┆ Pitlík, Josef               ┆ jk01093252    ┆ ["com"]        ┆ … ┆ null      ┆ null      ┆ 1975 ┆ 94    │
│ 1        ┆ Macourek, Miloš,            ┆ jk01072813    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1989 ┆ 139   │
│ 1        ┆ Steklač, Vojtěch,           ┆ jk01121138    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1982 ┆ 32    │
│ 1        ┆ Drijverová, Martina,        ┆ jk01023067    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1988 ┆ 59    │
│ 1        ┆ Taylor, David,              ┆ xx0028832     ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1992 ┆ 247   │
│ 1        ┆ Drijverová, Martina,        ┆ jk01023067    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 2012 ┆ 69    │
│ 1        ┆ Neff, Vladimír,             ┆ jk01082908    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1984 ┆ 288   │
│ 1        ┆ Hrnčíř, Svatopluk,          ┆ jk01042788    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1992 ┆ 54    │
│ 1        ┆ Nepil, František,           ┆ jk01083177    ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1989 ┆ 207   │
│ 1        ┆ Granin, Daniil              ┆ jn19990210255 ┆ ["aut"]        ┆ … ┆ null      ┆ null      ┆ 1962 ┆ 393   │
│          ┆ Aleksandrovič,              ┆               ┆                ┆   ┆           ┆           ┆      ┆       │
│ 1        ┆ Lindgren, Astrid,           ┆ jn19990005095

In [100]:
df.filter(pl.col('700_4') == 'ill').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (13_633, 2)
┌─────────────────────────────────┬───────┐
│ 700_a                           ┆ 245_a │
│ ---                             ┆ ---   │
│ str                             ┆ u32   │
╞═════════════════════════════════╪═══════╡
│ Born, Adolf,                    ┆ 281   │
│ Burian, Zdeněk,                 ┆ 230   │
│ Němeček, Jaroslav,              ┆ 179   │
│ Zmatlíková, Helena,             ┆ 164   │
│ Bouda, Cyril,                   ┆ 164   │
│ Winter-Neprakta, Jiří,          ┆ 160   │
│ Krejčová, Zdeňka,               ┆ 159   │
│ Šplíchal, Antonín,              ┆ 143   │
│ Thuma, Karel Ladislav,          ┆ 134   │
│ Černý, Věnceslav,               ┆ 133   │
│ Vydrová, Markéta,               ┆ 128   │
│ Plicková, Edita,                ┆ 124   │
│ Svolinský, Karel,               ┆ 123   │
│ Lada, Josef,                    ┆ 123   │
│ Študlarová, Zdeňka,             ┆ 122   │
│ Aleš, Mikoláš,                  ┆ 119   │
│ Petráček, Jiří,                 ┆ 108   │
│ Popprová, Andrea                ┆ 103   │
│ Lhoták, Kamil,                  ┆ 98    │
│ Scheiner, Artuš,                ┆ 96    │
│ Slíva, Jiří,                    ┆ 93    │
│ Jiránek, Vladimír,              ┆ 88    │
│ Trnka, Jiří,                    ┆ 87    │
│ Čuma, Aleš,                     ┆ 85    │
│ Janeček, Ota,                   ┆ 85    │
│ Hegerová, Vendula,              ┆ 84    │
│ Jakešová, Miroslava,            ┆ 84    │
│ Wowk, Jiří,                     ┆ 80    │
│ Schulz, Alena,                  ┆ 79    │
│ Tesař, Vladimír,                ┆ 79    │
│ Martenek, Miloslav,             ┆ 78    │
│ Fixl, Jiří,                     ┆ 78    │
│ Velčovský, Josef,               ┆ 77    │
│ Čutta, Václav,                  ┆ 76    │
│ Procházka, Otakar               ┆ 76    │
│ Teissig, Karel,                 ┆ 75    │
│ Kubašta, Vojtěch,               ┆ 75    │
│ Kratochvíl, Zdeněk,             ┆ 74    │
│ Škoda, František,               ┆ 74    │
│ Komárek, Vladimír,              ┆ 73    │
│ Kabát, Václav,                  ┆ 70    │
│ Hora, Jan,                      ┆ 70    │
│ Čapek, Josef,                   ┆ 68    │
│ Renčín, Vladimír,               ┆ 68    │
│ Poppr, Roman                    ┆ 68    │
│ Urban, Petr,                    ┆ 66    │
│ Franta, Karel,                  ┆ 66    │
│ Netopil, Zdeněk,                ┆ 66    │
│ Kalousek, Jiří,                 ┆ 65    │
│ Filcík, Gabriel,                ┆ 64    │
│ …                               ┆ …     │
│ Abril, Mauricio                 ┆ 1     │
│ Kuder, Aaron                    ┆ 1     │
│ Geraci, Drew                    ┆ 1     │
│ Babińska, Magdalena             ┆ 1     │
│ Honys, Josef,                   ┆ 1     │
│ Asciach, Marie-Laure,           ┆ 1     │
│ Dittmann, Johann,               ┆ 1     │
│ Vodička, Pavel,                 ┆ 1     │
│ Budík, Tomáš                    ┆ 1     │
│ Connell, Bridgit                ┆ 1     │
│ Taterová, Irena                 ┆ 1     │
│ Jančurová, Magdalena,           ┆ 1     │
│ Krawczak, Andrzej,              ┆ 1     │
│ Bartos, Anita                   ┆ 1     │
│ Krch, Martin,                   ┆ 1     │
│ Hlaváček, Lev                   ┆ 1     │
│ Babák, Miloš                    ┆ 1     │
│ Ferniani, Federico,             ┆ 1     │
│ Azaola, Jon Ander               ┆ 1     │
│ Beer, Sophie                    ┆ 1     │
│ Řehová, Iva,                    ┆ 1     │
│ Máchal, Jan                     ┆ 1     │
│ Šťastný, Pavel,                 ┆ 1     │
│ Diviš, Vladimír                 ┆ 1     │
│ Bordin, Claudia                 ┆ 1     │
│ Uhlík, Karel                    ┆ 1     │
│ Sargood, Corinna,               ┆ 1     │
│ Marcineková, Václava,           ┆ 1     │
│ Lancová, Kateřina,              ┆ 1     │
│ Jordanová, Soňa                 ┆ 1     │
│ Mai, Weitong                    ┆ 1     │
│ Lišková, Jana,                  ┆ 1     │
│ Martin, Frank,                  ┆ 1     │
│ Giotto di Bondone,              ┆ 1     │
│ Solařík, Karel,    

In [101]:
df_preklady = df.join(pl.read_parquet(os.path.join("data/cnb_sloupce","041.parquet")), left_on="001", right_on="001", how="left")

In [102]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (18_185, 2)
┌────────────────────────────┬───────┐
│ 700_a                      ┆ 245_a │
│ ---                        ┆ ---   │
│ str                        ┆ u32   │
╞════════════════════════════╪═══════╡
│ Butala, Tomáš,             ┆ 501   │
│ Pavka, Marek,              ┆ 427   │
│ Vyskočil, Josef            ┆ 335   │
│ Sladká, Stanislava         ┆ 246   │
│ Schönová, Zuzana           ┆ 234   │
│ Volhejnová, Veronika,      ┆ 230   │
│ Podaný, Richard,           ┆ 223   │
│ Kuťák, Jaroslav,           ┆ 214   │
│ Chromiaková, Eva           ┆ 196   │
│ Pacnerová, Jana,           ┆ 195   │
│ Štorkánová, Anna,          ┆ 179   │
│ Klůfová, Petra,            ┆ 168   │
│ Jašová, Jana,              ┆ 163   │
│ Dušek, Zdík,               ┆ 154   │
│ Kadlecová, Eva,            ┆ 148   │
│ Pokorný, Martin,           ┆ 140   │
│ Řežábek, Rudolf,           ┆ 140   │
│ Lacinová, Libuše,          ┆ 140   │
│ Dvořáková, Dagmar          ┆ 132   │
│ Kantůrek, Jan,             ┆ 130   │
│ Kozák, Jan,                ┆ 126   │
│ Smolaková, Helena          ┆ 126   │
│ Sychra, Pavel              ┆ 122   │
│ Führmann Vízdalová, Ivana, ┆ 119   │
│ Jovanovičová, Hana,        ┆ 118   │
│ Stach, Jiří,               ┆ 117   │
│ Stachová, Helena,          ┆ 117   │
│ Kufnerová, Zlata,          ┆ 117   │
│ Škultéty, Michaela,        ┆ 112   │
│ Žáček, Milan,              ┆ 111   │
│ Niklíčková, Alexandra,     ┆ 109   │
│ Somogyi, Viola,            ┆ 107   │
│ Vlčková, Jana,             ┆ 106   │
│ Weinfurter, Karel,         ┆ 106   │
│ Nuhlíčková, Ivana,         ┆ 105   │
│ Diestlerová, Petra,        ┆ 103   │
│ Vinšová, Kateřina,         ┆ 102   │
│ Krejčí, Hana               ┆ 102   │
│ Heller, František          ┆ 101   │
│ Faltejsková, Lenka,        ┆ 98    │
│ Brožová, Eva               ┆ 98    │
│ Hradil, Radomil,           ┆ 98    │
│ Schuster, R. K.            ┆ 95    │
│ Morávková, Alena,          ┆ 93    │
│ Rada, Jan                  ┆ 92    │
│ Novotná, Jana,             ┆ 92    │
│ Žák, Jiří,                 ┆ 92    │
│ Chodilová, Dana,           ┆ 92    │
│ Zábrana, Jan,              ┆ 91    │
│ Křivánková, Anna,          ┆ 89    │
│ …                          ┆ …     │
│ Vlachová, Milada           ┆ 1     │
│ Gabašová, Jitka,           ┆ 1     │
│ Minahane, John,            ┆ 1     │
│ Kalmus, Radovan            ┆ 1     │
│ Dvořák, Josef              ┆ 1     │
│ Draxl, Václav,             ┆ 1     │
│ Kupšovský, Jiří            ┆ 1     │
│ Rynešová, Marta,           ┆ 1     │
│ Holec, Petr,               ┆ 1     │
│ Novotný, Miloslav          ┆ 1     │
│ Sanetrníková, Martina,     ┆ 1     │
│ Kuchařová Kalná, Zdena,    ┆ 1     │
│ Smolková, Marie            ┆ 1     │
│ Hykš, Ondřej               ┆ 1     │
│ Pistorius, Petr            ┆ 1     │
│ Bohuslavová, Vendula       ┆ 1     │
│ Somerová, Kristýna         ┆ 1     │
│ Knor, Zlatko,              ┆ 1     │
│ Olchavová, Marie           ┆ 1     │
│ Holečková, Božena          ┆ 1     │
│ Černoušek, Michal,         ┆ 1     │
│ Marković, Zvjezdana        ┆ 1     │
│ Vihan, Stanislav,          ┆ 1     │
│ Kaštická, Daniela          ┆ 1     │
│ Dobeš, Josef,              ┆ 1     │
│ Horn, Zdeněk               ┆ 1     │
│ Pavlíček, Petr             ┆ 1     │
│ Budka, Jan,                ┆ 1     │
│ Martínek, Tomáš            ┆ 1     │
│ Kneblová, Barbora          ┆ 1     │
│ Hakl, Emil,                ┆ 1     │
│ Markalous, Evžen,          ┆ 1     │
│ Vlčková, Kateřina,         ┆ 1     │
│ Holičová, Irena            ┆ 1     │
│ Hedrlín, Antonín           ┆ 1     │
│ Křehla, Ladislav,          ┆ 1     │
│ Jenčíková, Agnesa Adriana, ┆ 1     │
│ Stádník, M.                ┆ 1     │
│ Cibulka, Radek,            ┆ 1     │
│ Štefanovič, Andrej         ┆ 1     │
│ Banýr, Jiří,               ┆ 1     │
│ Rychlík, Karel,            ┆ 1     │
│ Klement, M.                ┆ 1     │
│ Křikava, Louis,            ┆ 1     │
│ Kučera, Zdeněk,            ┆ 1     │
│ Úlovec, Jiří,              ┆ 1     │
│ T

In [103]:
df_preklady.filter(pl.col('700_a') == "Butala, Tomáš,").group_by("100_a").len()

shape: (33, 2)
┌────────────────────────────┬─────┐
│ 100_a                      ┆ len │
│ ---                        ┆ --- │
│ str                        ┆ u32 │
╞════════════════════════════╪═════╡
│ Czernin, Monika,           ┆ 1   │
│ Mortimer, Glenn            ┆ 4   │
│ Sinclair, Luke             ┆ 8   │
│ Fargo, Bill                ┆ 4   │
│ Shannon, Mark              ┆ 1   │
│ Silva, Tony,               ┆ 1   │
│ Bellmar, Elena,            ┆ 2   │
│ Morton, Jack               ┆ 6   │
│ Roberts, Dan,              ┆ 1   │
│ Warner, Hal,               ┆ 1   │
│ Lane, Lex                  ┆ 4   │
│ Robertson, Frank C.        ┆ 2   │
│ Murphy, Bill,              ┆ 10  │
│ Glaser, Frank              ┆ 9   │
│ Callahan, Frank            ┆ 2   │
│ Scott, William,            ┆ 141 │
│ Hayes, Rex,                ┆ 12  │
│ Arnaldur Indriðason,       ┆ 4   │
│ Taylor, Kathryn            ┆ 3   │
│ Gringel, Dana,             ┆ 1   │
│ Goga-Klinkenberg, Susanne, ┆ 4   │
│ Kutscher, Volker,          ┆ 10  │
│ Unger, Gert F.,            ┆ 387 │
│ Ryan, William              ┆ 4   │
│ Schröder, Rainer M.,       ┆ 1   │
│ Vermalle, Caroline,        ┆ 1   │
│ Denver, Jeff,              ┆ 1   │
│ Aurel, Catherine,          ┆ 1   │
│ Sharon, H. S.              ┆ 3   │
│ Benson, Robert             ┆ 2   │
│ Morgan, Matt               ┆ 4   │
│ Engel, Cornelia            ┆ 1   │
│ Schiewe, Ulf,              ┆ 1   │
└────────────────────────────┴─────┘

In [104]:
df_preklady.filter(pl.col('700_a') == "Butala, Tomáš,").group_by("041_h").len()

shape: (5, 2)
┌───────────┬─────┐
│ 041_h     ┆ len │
│ ---       ┆ --- │
│ list[str] ┆ u32 │
╞═══════════╪═════╡
│ null      ┆ 1   │
│ ["ger"]   ┆ 628 │
│ ["ice"]   ┆ 4   │
│ ["fre"]   ┆ 1   │
│ ["eng"]   ┆ 3   │
└───────────┴─────┘

In [105]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (18_185, 2)
┌─────────────────────────────┬───────┐
│ 700_a                       ┆ 245_a │
│ ---                         ┆ ---   │
│ str                         ┆ u32   │
╞═════════════════════════════╪═══════╡
│ Butala, Tomáš,              ┆ 501   │
│ Pavka, Marek,               ┆ 427   │
│ Vyskočil, Josef             ┆ 335   │
│ Sladká, Stanislava          ┆ 246   │
│ Schönová, Zuzana            ┆ 234   │
│ Volhejnová, Veronika,       ┆ 230   │
│ Podaný, Richard,            ┆ 223   │
│ Kuťák, Jaroslav,            ┆ 214   │
│ Chromiaková, Eva            ┆ 196   │
│ Pacnerová, Jana,            ┆ 195   │
│ Štorkánová, Anna,           ┆ 179   │
│ Klůfová, Petra,             ┆ 168   │
│ Jašová, Jana,               ┆ 163   │
│ Dušek, Zdík,                ┆ 154   │
│ Kadlecová, Eva,             ┆ 148   │
│ Řežábek, Rudolf,            ┆ 140   │
│ Pokorný, Martin,            ┆ 140   │
│ Lacinová, Libuše,           ┆ 140   │
│ Dvořáková, Dagmar           ┆ 132   │
│ Kantůrek, Jan,              ┆ 130   │
│ Kozák, Jan,                 ┆ 126   │
│ Smolaková, Helena           ┆ 126   │
│ Sychra, Pavel               ┆ 122   │
│ Führmann Vízdalová, Ivana,  ┆ 119   │
│ Jovanovičová, Hana,         ┆ 118   │
│ Kufnerová, Zlata,           ┆ 117   │
│ Stach, Jiří,                ┆ 117   │
│ Stachová, Helena,           ┆ 117   │
│ Škultéty, Michaela,         ┆ 112   │
│ Žáček, Milan,               ┆ 111   │
│ Niklíčková, Alexandra,      ┆ 109   │
│ Somogyi, Viola,             ┆ 107   │
│ Weinfurter, Karel,          ┆ 106   │
│ Vlčková, Jana,              ┆ 106   │
│ Nuhlíčková, Ivana,          ┆ 105   │
│ Diestlerová, Petra,         ┆ 103   │
│ Krejčí, Hana                ┆ 102   │
│ Vinšová, Kateřina,          ┆ 102   │
│ Heller, František           ┆ 101   │
│ Hradil, Radomil,            ┆ 98    │
│ Brožová, Eva                ┆ 98    │
│ Faltejsková, Lenka,         ┆ 98    │
│ Schuster, R. K.             ┆ 95    │
│ Morávková, Alena,           ┆ 93    │
│ Žák, Jiří,                  ┆ 92    │
│ Novotná, Jana,              ┆ 92    │
│ Chodilová, Dana,            ┆ 92    │
│ Rada, Jan                   ┆ 92    │
│ Zábrana, Jan,               ┆ 91    │
│ Křivánková, Anna,           ┆ 89    │
│ …                           ┆ …     │
│ Štolovský, Eduard V.,       ┆ 1     │
│ Mareš, Antonín,             ┆ 1     │
│ Kurz, Otakar                ┆ 1     │
│ Drozdová, Hana,             ┆ 1     │
│ Bělohradský, J. V.          ┆ 1     │
│ Tůma, Vladimír              ┆ 1     │
│ Pastuszak, Jarosław,        ┆ 1     │
│ Zábranská, Zdena,           ┆ 1     │
│ Sedláček, Richard           ┆ 1     │
│ Chodounský, Karel,          ┆ 1     │
│ Prentis, Thomas             ┆ 1     │
│ Bílá, E.                    ┆ 1     │
│ Schubert, Vojtěch,          ┆ 1     │
│ Vavrouchová, Jana           ┆ 1     │
│ Vodička, Antonín,           ┆ 1     │
│ Rodovský z Hustiřan, Bavor, ┆ 1     │
│ Kuťáková, Eva,              ┆ 1     │
│ Tropp, František,           ┆ 1     │
│ Fišerová-Slaninová, Petra   ┆ 1     │
│ Secký, Rudolf,              ┆ 1     │
│ Tráva, Jan                  ┆ 1     │
│ Babáček, Jan Fr.            ┆ 1     │
│ Němcová, Martina            ┆ 1     │
│ Moralesová, Alexandra,      ┆ 1     │
│ Štouračová, Alena           ┆ 1     │
│ Zrůstková, Petra            ┆ 1     │
│ Minařík, Stanislav          ┆ 1     │
│ Míšek, Ivan,                ┆ 1     │
│ Douša, Ladislav             ┆ 1     │
│ Kruven, J. M.               ┆ 1     │
│ Křižanová, Sylva            ┆ 1     │
│ Fischmannová, Judita        ┆ 1     │
│ Havlíček, Dušan,            ┆ 1     │
│ Skovron, Alex,              ┆ 1     │
│ Čajková, Irena              ┆ 1     │
│ Šimáková, Alice             ┆ 1     │
│ Klíma, Stanislav Václav,    ┆ 1     │
│ Hermannová, Kamila          ┆ 1     │
│ Hádková, Marie              ┆ 1     │
│ Zemek, Václav,              ┆ 1     │
│ Lavman, Cornelia            ┆ 1     │
│ Codr, Milan,                ┆ 1     │
│ Pavlů, Marie,               ┆ 1     │
│ Fliegl, Tomáš      

In [106]:
df_preklady.filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("stran").sum()).sort(by="stran",descending=True)

shape: (18_185, 2)
┌─────────────────────────────────┬────────┐
│ 700_a                           ┆ stran  │
│ ---                             ┆ ---    │
│ str                             ┆ i64    │
╞═════════════════════════════════╪════════╡
│ Volhejnová, Veronika,           ┆ 104086 │
│ Pacnerová, Jana,                ┆ 90284  │
│ Kantůrek, Jan,                  ┆ 80551  │
│ Podaný, Richard,                ┆ 75994  │
│ Dušek, Zdík,                    ┆ 68357  │
│ Klůfová, Petra,                 ┆ 68070  │
│ Jašová, Jana,                   ┆ 66951  │
│ Chodilová, Dana,                ┆ 56060  │
│ Medek, Pavel,                   ┆ 54195  │
│ Bartošková, Linda,              ┆ 53632  │
│ Řežábek, Rudolf,                ┆ 51852  │
│ Kobělka, Jiří,                  ┆ 50248  │
│ Pokorný, Martin,                ┆ 49472  │
│ Butala, Tomáš,                  ┆ 47622  │
│ Hron, Zdeněk,                   ┆ 45346  │
│ Zaorálek, Jaroslav,             ┆ 44228  │
│ Kotrle, Petr,                   ┆ 44222  │
│ Führmann Vízdalová, Ivana,      ┆ 43707  │
│ Krejčová, Dana                  ┆ 43672  │
│ Kozák, Jan,                     ┆ 43670  │
│ Faltejsková, Lenka,             ┆ 42989  │
│ Kadlecová, Eva,                 ┆ 42772  │
│ Trávníček, Luboš,               ┆ 42489  │
│ Kondrysová, Eva,                ┆ 41792  │
│ Žáček, Milan,                   ┆ 41130  │
│ Ľalíková, Zuzana,               ┆ 41108  │
│ Krištůfková, Kateřina,          ┆ 40202  │
│ Medek, Vladimír,                ┆ 39039  │
│ Jindrová, Alena,                ┆ 37979  │
│ Míček, Dalibor,                 ┆ 37961  │
│ Křivánková, Anna,               ┆ 37329  │
│ Trávníčková, Libuše,            ┆ 37257  │
│ Zábrana, Jan,                   ┆ 36956  │
│ Brožová, Eva                    ┆ 36699  │
│ Vlčková, Jana,                  ┆ 36391  │
│ Houbová, Věra,                  ┆ 35662  │
│ Heller, František               ┆ 35560  │
│ Moserová, Jaroslava,            ┆ 35535  │
│ Žák, Jiří,                      ┆ 35332  │
│ Nuhlíčková, Ivana,              ┆ 34922  │
│ Weinfurter, Karel,              ┆ 34763  │
│ Stárková, Jiřina                ┆ 34565  │
│ Wolfová, Zora,                  ┆ 34555  │
│ Bičíková, Romana,               ┆ 34246  │
│ Křístková, Eva                  ┆ 34049  │
│ Tilsch, Emanuel,                ┆ 33415  │
│ Marková, Michala,               ┆ 33354  │
│ Niklíčková, Alexandra,          ┆ 33232  │
│ Jindra, Miroslav,               ┆ 32742  │
│ Dvořák, Libor,                  ┆ 32490  │
│ …                               ┆ …      │
│ Metličková, Kristýna            ┆ 1      │
│ Podavka, Ondřej,                ┆ 1      │
│ Pol'ko, Ol'ga Volodymyrìvna     ┆ 1      │
│ Mostova, Julìja Mykolajivna     ┆ 1      │
│ Horáček, Pavel,                 ┆ 1      │
│ Vavruška, Jindřich              ┆ 1      │
│ Děcká, Eliška,                  ┆ 1      │
│ Dyčková, Alžběta,               ┆ 1      │
│ Bednářová, Lucie                ┆ 1      │
│ Vaněčková, Vladislava,          ┆ 1      │
│ Zoban, Petr,                    ┆ 1      │
│ Jirošová, Barbora               ┆ 1      │
│ Desenská Ciglerová, Jana        ┆ 1      │
│ Hofman, Petr,                   ┆ 1      │
│ Phamová, Hau,                   ┆ 1      │
│ Lukaštíková, Julie,             ┆ 1      │
│ Jelínek, Konstantin,            ┆ 1      │
│ Maxová, Pavla                   ┆ 1      │
│ Pavlisová, Hana                 ┆ 1      │
│ Rohoža, Anna Vìktorìvna         ┆ 1      │
│ Ivancìv, Galyna Volodymyrìvna   ┆ 1      │
│ Kohnerová, Lucie                ┆ 1      │
│ Geislerová, Gabriela            ┆ 1      │
│ Velká, Tereza                   ┆ 1      │
│ Kadlecová, Ester,               ┆ 1      │
│ Raveane, Drahomíra              ┆ 1      │
│ Novotná, Eliška                 ┆ 1      │
│ Tenaud, Guillaume,              ┆ 1      │
│ Kaszonyi, Pavol                 ┆ 1      │
│ Petrunìna, Julìja Andrìjivna    ┆ 1      │
│ Kim, Mina                       ┆ 1      │
│ Pelc, Vojtěch                   ┆ 1      │
│ Dudzik, Pavel      

In [107]:
df_preklady.filter(pl.col('700_a') == "Volhejnová, Veronika,").group_by("100_a").len().sort(by="len",descending=True)

shape: (106, 2)
┌────────────────────────┬─────┐
│ 100_a                  ┆ len │
│ ---                    ┆ --- │
│ str                    ┆ u32 │
╞════════════════════════╪═════╡
│ Kinney, Jeff,          ┆ 52  │
│ Christie, Agatha,      ┆ 29  │
│ Herbert, Frank,        ┆ 24  │
│ Lewis, C. S.           ┆ 21  │
│ Walliams, David,       ┆ 21  │
│ Green, John,           ┆ 17  │
│ Colfer, Chris,         ┆ 16  │
│ Le Carré, John,        ┆ 8   │
│ Morse, Brian,          ┆ 7   │
│ Grisham, John,         ┆ 6   │
│ Hannah, Sophie,        ┆ 6   │
│ Cunningham, Michael,   ┆ 5   │
│ Eason, Cassandra,      ┆ 5   │
│ Atkinson, Kate,        ┆ 5   │
│ Andrews, William W.    ┆ 4   │
│ Daldry, Jeremy,        ┆ 4   │
│ Russell, Rachel Renée  ┆ 4   │
│ Peters, Helen          ┆ 4   │
│ Clarke, Arthur C.      ┆ 4   │
│ Piers, Helen           ┆ 4   │
│ Asimov, Isaac,         ┆ 3   │
│ Allison, Jennifer,     ┆ 3   │
│ Smith, James,          ┆ 3   │
│ Colfer, Eoin,          ┆ 3   │
│ Novik, Naomi,          ┆ 3   │
│ Brown, Sandra,         ┆ 3   │
│ Herbert, Brian,        ┆ 3   │
│ Crichton, Michael,     ┆ 3   │
│ Lamb, Kathryn,         ┆ 3   │
│ Anderson, Poul,        ┆ 3   │
│ Barnes, Jennifer Lynn, ┆ 3   │
│ Levin, Ira,            ┆ 2   │
│ Thomson, Jamie,        ┆ 2   │
│ Twain, Mark,           ┆ 2   │
│ Rich, Roberta,         ┆ 2   │
│ Chee, Traci            ┆ 2   │
│ Smale, Holly,          ┆ 2   │
│ Kalfař, Jaroslav,      ┆ 2   │
│ Kaplický, Jan,         ┆ 2   │
│ Crouch, Blake,         ┆ 2   │
│ Johansen, Erika        ┆ 2   │
│ King, Andrew           ┆ 2   │
│ George, Elizabeth,     ┆ 2   │
│ Mercree, Amy Leigh,    ┆ 2   │
│ Adeyemi, Tomi,         ┆ 2   │
│ McKinlay, Deborah      ┆ 2   │
│ Rennison, Louise,      ┆ 1   │
│ Quirk, Lawrence J.,    ┆ 1   │
│ Matheson, Richard,     ┆ 1   │
│ Pollard, Michael,      ┆ 1   │
│ …                      ┆ …   │
│ Kostova, Elizabeth,    ┆ 1   │
│ Cornell, Paul,         ┆ 1   │
│ Lee, Suh Yoon          ┆ 1   │
│ Durrant, Sabine        ┆ 1   │
│ McIntyre, Anne,        ┆ 1   │
│ Levithan, David,       ┆ 1   │
│ Extence, Gavin,        ┆ 1   │
│ Hubbard, L. Ron        ┆ 1   │
│ Kowitt, Holly          ┆ 1   │
│ Fuller, Claire,        ┆ 1   │
│ Delany, Samuel R.,     ┆ 1   │
│ Scott, Joanna,         ┆ 1   │
│ Nelson, Jandy,         ┆ 1   │
│ Zhang, Amy,            ┆ 1   │
│ Ross, JoAnn            ┆ 1   │
│ Walls, Jeannette,      ┆ 1   │
│ Reed, Henry,           ┆ 1   │
│ Bryant, Dani           ┆ 1   │
│ Silverberg, Robert,    ┆ 1   │
│ Hornak, Francesca      ┆ 1   │
│ Marshall, David        ┆ 1   │
│ Larwood, Kieran        ┆ 1   │
│ Setterfield, Diane,    ┆ 1   │
│ Donoghue, Emma,        ┆ 1   │
│ La Fontaine, Jean de,  ┆ 1   │
│ Kissick, Lucy          ┆ 1   │
│ Brooks, Kevin,         ┆ 1   │
│ Shaheen, Michael A.    ┆ 1   │
│ Piedilato, Janet       ┆ 1   │
│ Oula, Valerie          ┆ 1   │
│ Graham, Caroline,      ┆ 1   │
│ Flinn, Alex,           ┆ 1   │
│ Kuttner, Henry,        ┆ 1   │
│ Michaels, Stase        ┆ 1   │
│ Peterson, Jordan B.,   ┆ 1   │
│ Forleo, Marie          ┆ 1   │
│ Kvítek, Martin,        ┆ 1   │
│ Jerome, Jerome K.      ┆ 1   │
│ Abrams, Stacey,        ┆ 1   │
│ Moore, Alan,           ┆ 1   │
│ Garber, Joseph R.,     ┆ 1   │
│ Josephs, Ray           ┆ 1   │
│ Anderson, Kevin J.,    ┆ 1   │
│ Laurie, Meshel,        ┆ 1   │
│ Cooper, Rose           ┆ 1   │
│ Winterson, Jeanette,   ┆ 1   │
│ Cornelius, Geoffrey    ┆ 1   │
│ Poe, Edgar Allan,      ┆ 1   │
│ Neubauer, Bonnie       ┆ 1   │
│ Hedsel, Mark,          ┆ 1   │
└────────────────────────┴─────┘

In [108]:
df_preklady.explode("041_h").filter(pl.col('700_4') == 'trl').group_by('700_a').agg(pl.col("041_h").n_unique()).sort(by="041_h",descending=True)

shape: (18_185, 2)
┌─────────────────────────┬───────┐
│ 700_a                   ┆ 041_h │
│ ---                     ┆ ---   │
│ str                     ┆ u32   │
╞═════════════════════════╪═══════╡
│ Babler, Otto František, ┆ 19    │
│ Hiršal, Josef,          ┆ 16    │
│ Vetti, O. S.,           ┆ 16    │
│ Vrchlický, Jaroslav,    ┆ 12    │
│ Bednář, Kamil,          ┆ 12    │
│ Vladislav, Jan,         ┆ 11    │
│ Kosterka, Hugo,         ┆ 11    │
│ Fischer, Otokar,        ┆ 11    │
│ Žáček, Jiří,            ┆ 11    │
│ Žilina, Miloslav,       ┆ 11    │
│ Sýs, Karel,             ┆ 11    │
│ Hrubín, František,      ┆ 10    │
│ Eisner, Pavel,          ┆ 10    │
│ Stankovský, Josef Jiří, ┆ 9     │
│ Hackenschmied, Hanuš,   ┆ 9     │
│ Borecký, Jaromír,       ┆ 9     │
│ Karpatský, Dušan,       ┆ 9     │
│ Štroblová, Jana,        ┆ 9     │
│ Pešková, Eliška,        ┆ 8     │
│ Mathesius, Bohumil,     ┆ 8     │
│ Somogyi, Viola,         ┆ 8     │
│ Mertlík, Rudolf,        ┆ 8     │
│ Kundera, Ludvík,        ┆ 8     │
│ Závada, Vilém,          ┆ 8     │
│ Vrátný, Karel,          ┆ 8     │
│ Kubišta, Luděk,         ┆ 8     │
│ Vrbová, Hana,           ┆ 8     │
│ Weinfurter, Karel,      ┆ 8     │
│ Vyskočil, Josef         ┆ 8     │
│ Pelán, Jiří,            ┆ 8     │
│ Novotný, Václav Juda,   ┆ 8     │
│ Vacek, Jindřich,        ┆ 8     │
│ Čvančara, Karel,        ┆ 8     │
│ Sládek, Josef Václav,   ┆ 8     │
│ Renč, Václav,           ┆ 8     │
│ Pokorný, Jaroslav,      ┆ 8     │
│ Šádek, František,       ┆ 8     │
│ Zbavitel, Dušan,        ┆ 8     │
│ Seifert, Viktor O. J.   ┆ 7     │
│ Nowak, Antonín,         ┆ 7     │
│ Škultéty, Michaela,     ┆ 7     │
│ Černý, Václav A.,       ┆ 7     │
│ Krausová-Lesná, Milada, ┆ 7     │
│ Skalický, Jaroslav,     ┆ 7     │
│ Peška, Bedřich,         ┆ 7     │
│ Frýbort, Zdeněk,        ┆ 7     │
│ Mattuš, Jan,            ┆ 7     │
│ Peisertová, Alena       ┆ 7     │
│ Pokorný, Jindřich,      ┆ 7     │
│ Kunstovný, Otakar,      ┆ 7     │
│ …                       ┆ …     │
│ Mervart, Miroslav,      ┆ 1     │
│ Hraše, Jan,             ┆ 1     │
│ Laudátová, Zdenka       ┆ 1     │
│ Bodnárová, Jana,        ┆ 1     │
│ Kašparová, Martina      ┆ 1     │
│ Miltnerová, Věra        ┆ 1     │
│ Beneš, Stanislav        ┆ 1     │
│ Fuchs, Alfréd,          ┆ 1     │
│ Nováková, Jitka         ┆ 1     │
│ Vavruška, Karel         ┆ 1     │
│ Dungel, Jan             ┆ 1     │
│ Pazourek, Jaroslav,     ┆ 1     │
│ Kobrle, Karel,          ┆ 1     │
│ Mandíková, Hana         ┆ 1     │
│ Ryšavý, Ladislav,       ┆ 1     │
│ Přecechtěl, Antonín,    ┆ 1     │
│ Štičková, An,           ┆ 1     │
│ Böswart, Štěpán,        ┆ 1     │
│ Hofmannová, Irena       ┆ 1     │
│ Pokorná, Růžena         ┆ 1     │
│ Feldstein, Valter,      ┆ 1     │
│ Zachová, Jiřina         ┆ 1     │
│ Čapková, Lucie          ┆ 1     │
│ Enoc, Josef             ┆ 1     │
│ Literáková, Martina     ┆ 1     │
│ Večeřa, Jan             ┆ 1     │
│ Kolčev, Ivan            ┆ 1     │
│ Krásenská, Klára,       ┆ 1     │
│ Zouhar, Jan,            ┆ 1     │
│ Tlustá, Vendula         ┆ 1     │
│ Blahutová, Ivana,       ┆ 1     │
│ Janda, Jiří,            ┆ 1     │
│ Fujimoto, Yoko          ┆ 1     │
│ Doutlík, Miroslav,      ┆ 1     │
│ Hofman, Petr,           ┆ 1     │
│ Moravec, Jan,           ┆ 1     │
│ Šupová, Marie           ┆ 1     │
│ Dietrich, Sven          ┆ 1     │
│ Dejdar, Břetislav,      ┆ 1     │
│ Zajíc, Jiří             ┆ 1     │
│ Hitschmann, Ota         ┆ 1     │
│ Krejčí, Jan             ┆ 1     │
│ Grušová, Anna           ┆ 1     │
│ Valentinová, Lucie      ┆ 1     │
│ Volná, Gražyna Milena,  ┆ 1     │
│ Auředníčková, Anna,     ┆ 1     │
│ Klouda, Antonín,        ┆ 1     │
│ Kieswetter, Miloš,      ┆ 1     │
│ Ježková, Blanka,        ┆ 1     │
│ Špicová, Zuzana         ┆ 1     │
└─────────────────────────┴───────┘

In [109]:
df_preklady.filter(pl.col('700_a') == "Babler, Otto František,").group_by('041_h').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (20, 2)
┌─────────────────────────┬───────┐
│ 041_h                   ┆ 245_a │
│ ---                     ┆ ---   │
│ list[str]               ┆ u32   │
╞═════════════════════════╪═══════╡
│ ["eng"]                 ┆ 10    │
│ ["ger"]                 ┆ 9     │
│ ["fre"]                 ┆ 8     │
│ null                    ┆ 5     │
│ ["scr"]                 ┆ 5     │
│ ["hrv"]                 ┆ 3     │
│ ["ita"]                 ┆ 3     │
│ ["bul"]                 ┆ 2     │
│ ["rus"]                 ┆ 2     │
│ ["lat"]                 ┆ 2     │
│ ["und"]                 ┆ 2     │
│ ["srp"]                 ┆ 2     │
│ ["lit"]                 ┆ 1     │
│ ["dut"]                 ┆ 1     │
│ ["pol"]                 ┆ 1     │
│ ["hrv", "slv", … "mac"] ┆ 1     │
│ ["fre", "eng"]          ┆ 1     │
│ ["cze"]                 ┆ 1     │
│ ["fro"]                 ┆ 1     │
│ ["slv"]                 ┆ 1     │
└─────────────────────────┴───────┘

In [110]:
df_preklady.filter(pl.col('700_a') == "Hiršal, Josef,").group_by('041_h').agg(pl.col("245_a").n_unique()).sort(by="245_a",descending=True)

shape: (20, 2)
┌────────────────┬───────┐
│ 041_h          ┆ 245_a │
│ ---            ┆ ---   │
│ list[str]      ┆ u32   │
╞════════════════╪═══════╡
│ ["ger"]        ┆ 32    │
│ null           ┆ 12    │
│ ["por"]        ┆ 4     │
│ ["spa"]        ┆ 3     │
│ ["scr"]        ┆ 2     │
│ ["fre"]        ┆ 2     │
│ ["rum"]        ┆ 2     │
│ ["swe"]        ┆ 2     │
│ ["mul"]        ┆ 2     │
│ ["chi"]        ┆ 1     │
│ ["pal"]        ┆ 1     │
│ ["por", "fre"] ┆ 1     │
│ ["por", "eng"] ┆ 1     │
│ ["eng"]        ┆ 1     │
│ ["scc"]        ┆ 1     │
│ ["per"]        ┆ 1     │
│ ["rus"]        ┆ 1     │
│ ["hun"]        ┆ 1     │
│ ["hrv"]        ┆ 1     │
│ ["nor"]        ┆ 1     │
└────────────────┴───────┘